In [8]:
# БАЗОВЫЕ БИБЛИОТЕКИ
import os
import math
import time

# БИБЛИОТЕКИ ДЛЯ РАБОТЫ С ДАННЫМИ
import numpy as np
import pandas as pd
import json

# БИБЛИОТЕКИ ДЛЯ СТАТ. АНАЛИЗА
import scipy
import scipy.stats as stats
import statsmodels.api as sm
from statsmodels.formula.api import ols
import statsmodels.formula.api as smf
from patsy import dmatrices
import numpy.polynomial as poly

# БИБЛИОТЕКИ ДЛЯ ВИЗУАЛИЗАЦИИ
import seaborn as sns
import matplotlib.pyplot as plt

import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots

In [2]:
colors = px.colors.qualitative.T10_r
colors

['#BAB0AC',
 '#9D755D',
 '#FF9DA6',
 '#B279A2',
 '#EECA3B',
 '#54A24B',
 '#72B7B2',
 '#E45756',
 '#F58518',
 '#4C78A8']

# 0) Загрузка данных

In [3]:
data_archive = pd.read_excel(r"D:\Работа\Кодинг\Проекты ML и NN\ML_Projects\Олимпиады\DANO\Заключительный этап 2023-2024\Данные\central_bank_dataset.xlsx")
data_archive

Unnamed: 0      X  id_w        id_i                    psu  \
0               0      1  2022     1000101  Ленинградская область   
1               1      2  2022     1000102  Ленинградская область   
2               2      3  2022     1000502  Ленинградская область   
3               3      4  2022     1000604  Ленинградская область   
4               4      5  2022     1000701  Ленинградская область   
...           ...    ...   ...         ...                    ...   
12157       12157  12158  2022  1351071205     Смоленская область   
12158       12158  12159  2022   138930501              г. Москва   
12159       12159  12160  2022   138930502              г. Москва   
12160       12160  12161  2022   138930505              г. Москва   
12161       12161  12162  2022  1429041401     Московская область   

               gr_vozr                   gr_educ sett_typ  \
0            46-55 лет       Среднее специальное    Город   
1            46-55 лет      Среднее общее и ниже    Город   
2            26-35 лет      Среднее общее и ниже    Город   
3            18-25 лет       Среднее специальное    Город   
4      56 лет и старше  Высшее и неполное высшее    Город   
...                ...                       ...      ...   
12157        36-45 лет      Среднее общее и ниже    Город   
12158        36-45 лет      Среднее общее и ниже    Город   
12159        18-25 лет      Среднее общее и ниже    Город   
12160  56 лет и старше      Среднее общее и ниже    Город   
12161        36-45 лет  Высшее и неполное высшее    Город   

                                  size     i_h4  ...  c44a_3_s_r p96_1 p911_1  \
0       от 10 тыс.чел. до 100 тыс.чел.  ЖЕНСКИЙ  ...         NaN   NaN    NaN   
1       от 10 тыс.чел. до 100 тыс.чел.  МУЖСКОЙ  ...         NaN   NaN    NaN   
2       от 10 тыс.чел. до 100 тыс.чел.  МУЖСКОЙ  ...         NaN   NaN    NaN   
3       от 10 тыс.чел. до 100 тыс.чел.  МУЖСКОЙ  ...         NaN     6   9000   
4       от 10 тыс.чел. до 100 тыс.чел.  ЖЕНСКИЙ  ...         NaN   NaN    NaN   
...                                ...      ...  ...         ...   ...    ...   
12157  от 100 тыс.чел. до 500 тыс.чел.  МУЖСКОЙ  ...         NaN   NaN    NaN   
12158                         г.Москва  ЖЕНСКИЙ  ...         NaN   NaN    NaN   
12159                         г.Москва  ЖЕНСКИЙ  ...         NaN   NaN    NaN   
12160                         г.Москва  ЖЕНСКИЙ  ...         NaN   NaN    NaN   
12161  от 100 тыс.чел. до 500 тыс.чел.  ЖЕНСКИЙ  ...         NaN   NaN    NaN   

      p911a1 p911a1_s_r p911a2 p911a2_s_r p911a3 p911a3_s_r  \
0        NaN        NaN    NaN        NaN    NaN        NaN   
1        NaN        NaN    NaN        NaN    NaN        NaN   
2        NaN        NaN    NaN        NaN    NaN        NaN   
3        NaN     9000.0    NaN        NaN    NaN        NaN   
4        NaN        NaN    NaN        NaN    NaN        NaN   
...      ...        ...    ...        ...    ...        ...   
12157    NaN        NaN    NaN        NaN    NaN        NaN   
12158    NaN        NaN    NaN        NaN    NaN        NaN   
12159    NaN        NaN    NaN        NaN    NaN        NaN   
12160    NaN        NaN    NaN        NaN    NaN        NaN   
12161    NaN        NaN    NaN        NaN    NaN        NaN   

                                  k68  
0                    ТРАНСПОРТ, СВЯЗЬ  
1                    ТРАНСПОРТ, СВЯЗЬ  
2                       СТРОИТЕЛЬСТВО  
3      ТОРГОВЛЯ, БЫТОВОЕ ОБСЛУЖИВАНИЕ  
4                     ЗДРАВООХРАНЕНИЕ  
...                               ...  
12157                             NaN  
12158                             NaN  
12159  ТОРГОВЛЯ, БЫТОВОЕ ОБСЛУЖИВАНИЕ  
12160                             NaN  
12161        ОПЕРАЦИИ С НЕДВИЖИМОСТЬЮ  

[12162 rows x 121 columns]

In [4]:
data_archive["i_h5"]

0        1968
1        1975
2        1990
3        1997
4        1957
         ... 
12157    1980
12158    1978
12159    2004
12160    1955
12161    1978
Name: i_h5, Length: 12162, dtype: int64

In [5]:
data = pd.read_excel(r"D:\Работа\Кодинг\Проекты ML и NN\ML_Projects\Олимпиады\DANO\Заключительный этап 2023-2024\Данные\central_bank_dataset_full.xlsx")
data

ID   Gender                 Region        Age group  \
0         1000101  ЖЕНСКИЙ  Ленинградская область        46-55 лет   
1         1000102  МУЖСКОЙ  Ленинградская область        46-55 лет   
2         1000502  МУЖСКОЙ  Ленинградская область        26-35 лет   
3         1000604  МУЖСКОЙ  Ленинградская область        18-25 лет   
4         1000701  ЖЕНСКИЙ  Ленинградская область  56 лет и старше   
...           ...      ...                    ...              ...   
12157  1351071205  МУЖСКОЙ     Смоленская область        36-45 лет   
12158   138930501  ЖЕНСКИЙ              г. Москва        36-45 лет   
12159   138930502  ЖЕНСКИЙ              г. Москва        18-25 лет   
12160   138930505  ЖЕНСКИЙ              г. Москва  56 лет и старше   
12161  1429041401  ЖЕНСКИЙ     Московская область        36-45 лет   

                      Education                       Job field  \
0           Среднее специальное                ТРАНСПОРТ, СВЯЗЬ   
1          Среднее общее и ниже                ТРАНСПОРТ, СВЯЗЬ   
2          Среднее общее и ниже                   СТРОИТЕЛЬСТВО   
3           Среднее специальное  ТОРГОВЛЯ, БЫТОВОЕ ОБСЛУЖИВАНИЕ   
4      Высшее и неполное высшее                 ЗДРАВООХРАНЕНИЕ   
...                         ...                             ...   
12157      Среднее общее и ниже                             NaN   
12158      Среднее общее и ниже                             NaN   
12159      Среднее общее и ниже  ТОРГОВЛЯ, БЫТОВОЕ ОБСЛУЖИВАНИЕ   
12160      Среднее общее и ниже                             NaN   
12161  Высшее и неполное высшее        ОПЕРАЦИИ С НЕДВИЖИМОСТЬЮ   

                                             Type of job  \
0             ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
1             ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
2      ВЫ ЗАНИМАЕТЕСЬ ПРЕДПРИНИМАТЕЛЬСТВОМ ИЛИ ИНДИВИ...   
3             ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
4                                                    NaN   
...                                                  ...   
12157                                                NaN   
12158                                                NaN   
12159         ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
12160                                                NaN   
12161         ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   

                                           Relationship Type of residence  \
0                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ             Город   
1                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ             Город   
2                                           РАЗВЕДЕН(А)             Город   
3      НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)             Город   
4                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ             Город   
...                                                 ...               ...   
12157                                       РАЗВЕДЕН(А)             Город   
12158                                       РАЗВЕДЕН(А)             Город   
12159  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)             Город   
12160                                      ВДОВЕЦ/ВДОВА             Город   
12161                                       РАЗВЕДЕН(А)             Город   

                     Size of residence  ...  \
0       от 10 тыс.чел. до 100 тыс.чел.  ...   
1       от 10 тыс.чел. до 100 тыс.чел.  ...   
2       от 10 тыс.чел. до 100 тыс.чел.  ...   
3       от 10 тыс.чел. до 100 тыс.чел.  ...   
4       от 10 тыс.чел. до 100 тыс.чел.  ...   
...                                ...  ...   
12157  от 100 тыс.чел. до 500 тыс.чел.  ...   
12158                         г.Москва  ...   
12159                         г.Москва  ...   
12160                         г.Москва  ...   
12161  от 100 тыс.чел. до 500 тыс.чел.  ...   

                                      FK2                                FK3  \
0      ЧЕМ ВЫШЕ ДОХОДНОСТЬ, ТЕМ ВЫШЕ РИСК          СТАВКА ЦЕНТРАЛЬНОГО БАНКА  

In [6]:
ages = []

for age in data_archive["i_h5"]:
    ages.append(2022 - int(age))

data["Age"] = ages
data

ID   Gender                 Region        Age group  \
0         1000101  ЖЕНСКИЙ  Ленинградская область        46-55 лет   
1         1000102  МУЖСКОЙ  Ленинградская область        46-55 лет   
2         1000502  МУЖСКОЙ  Ленинградская область        26-35 лет   
3         1000604  МУЖСКОЙ  Ленинградская область        18-25 лет   
4         1000701  ЖЕНСКИЙ  Ленинградская область  56 лет и старше   
...           ...      ...                    ...              ...   
12157  1351071205  МУЖСКОЙ     Смоленская область        36-45 лет   
12158   138930501  ЖЕНСКИЙ              г. Москва        36-45 лет   
12159   138930502  ЖЕНСКИЙ              г. Москва        18-25 лет   
12160   138930505  ЖЕНСКИЙ              г. Москва  56 лет и старше   
12161  1429041401  ЖЕНСКИЙ     Московская область        36-45 лет   

                      Education                       Job field  \
0           Среднее специальное                ТРАНСПОРТ, СВЯЗЬ   
1          Среднее общее и ниже                ТРАНСПОРТ, СВЯЗЬ   
2          Среднее общее и ниже                   СТРОИТЕЛЬСТВО   
3           Среднее специальное  ТОРГОВЛЯ, БЫТОВОЕ ОБСЛУЖИВАНИЕ   
4      Высшее и неполное высшее                 ЗДРАВООХРАНЕНИЕ   
...                         ...                             ...   
12157      Среднее общее и ниже                             NaN   
12158      Среднее общее и ниже                             NaN   
12159      Среднее общее и ниже  ТОРГОВЛЯ, БЫТОВОЕ ОБСЛУЖИВАНИЕ   
12160      Среднее общее и ниже                             NaN   
12161  Высшее и неполное высшее        ОПЕРАЦИИ С НЕДВИЖИМОСТЬЮ   

                                             Type of job  \
0             ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
1             ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
2      ВЫ ЗАНИМАЕТЕСЬ ПРЕДПРИНИМАТЕЛЬСТВОМ ИЛИ ИНДИВИ...   
3             ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
4                                                    NaN   
...                                                  ...   
12157                                                NaN   
12158                                                NaN   
12159         ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   
12160                                                NaN   
12161         ВЫ РАБОТАЕТЕ НА ПРЕДПРИЯТИИ, В ОРГАНИЗАЦИИ   

                                           Relationship Type of residence  \
0                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ             Город   
1                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ             Город   
2                                           РАЗВЕДЕН(А)             Город   
3      НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)             Город   
4                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ             Город   
...                                                 ...               ...   
12157                                       РАЗВЕДЕН(А)             Город   
12158                                       РАЗВЕДЕН(А)             Город   
12159  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)             Город   
12160                                      ВДОВЕЦ/ВДОВА             Город   
12161                                       РАЗВЕДЕН(А)             Город   

                     Size of residence  ...  \
0       от 10 тыс.чел. до 100 тыс.чел.  ...   
1       от 10 тыс.чел. до 100 тыс.чел.  ...   
2       от 10 тыс.чел. до 100 тыс.чел.  ...   
3       от 10 тыс.чел. до 100 тыс.чел.  ...   
4       от 10 тыс.чел. до 100 тыс.чел.  ...   
...                                ...  ...   
12157  от 100 тыс.чел. до 500 тыс.чел.  ...   
12158                         г.Москва  ...   
12159                         г.Москва  ...   
12160                         г.Москва  ...   
12161  от 100 тыс.чел. до 500 тыс.чел.  ...   

                                     FK3  FK4  FK5  FK6  \
0              СТАВКА ЦЕНТРАЛЬНОГО БАНКА  Нет  Нет  Нет   
1              СТАВКА ЦЕНТРАЛЬНОГО БАНКА

In [7]:
coeffs = pd.read_csv(r"D:\Работа\Кодинг\Проекты ML и NN\ML_Projects\Олимпиады\DANO\Заключительный этап 2023-2024\Данные\new_coeffs.csv")
coeffs

Unnamed: 0          ID  Active in debts and bonds  \
0               0     1000101                          3   
1               1     1000102                          4   
2               2     1000502                          4   
3               3     1000604                          2   
4               4     1000701                          3   
...           ...         ...                        ...   
12157       12157  1351071205                          0   
12158       12158   138930501                          1   
12159       12159   138930502                          1   
12160       12160   138930505                          1   
12161       12161  1429041401                          4   

       New Active in debts and bonds  Internet usage level  Financial level  \
0                                  3                  1.25                4   
1                                  4                  1.25                3   
2                                  4                  4.75                2   
3                                  2                  1.25                6   
4                                  3                  1.25                2   
...                              ...                   ...              ...   
12157                              0                  0.00                6   
12158                              1                  1.25                5   
12159                              1                  1.25                4   
12160                              1                  0.00                3   
12161                              4                  1.25                6   

       Financial level %  
0                     57  
1                     43  
2                     29  
3                     86  
4                     29  
...                  ...  
12157                 86  
12158                 71  
12159                 57  
12160                 43  
12161                 86  

[12162 rows x 7 columns]

# ПРЕДЗАЩИТА ПРОШЛА:

* ОСНОВНАЯ ГИПОТЕЗА - НЕЛИНЕЙНАЯ ЗАВИСИМОСТЬ ПЕРЕМЕННОЙ ИНДЕКСА ФИНАНСОВОЙ ГРАМОТНОСТИ ОТ ВОЗРАСТА РЕСПОНДЕНТОВ

Проверка предположения о возможной линейной зависимости между исследуемыми переменными может проверяться с помощью коэффициентов детерминации r2 полиномиальной и линейных регрессиий. Для этого необходимо провести регрессионный анализ.

В виде таргетированной переменной будет использоваться индекс финансовой грамотности, измеренный в процентах, а в качестве факторной переменной - возраст респондента.

Обе переменные соответсвуют основным условиям для применения линейной регрессии: 
1. Значения индекса фин. грамотности и возраста расположены в достаточно широком диапозоне
2. Распределения переменных напоминают нормальное (графики ниже)
3. Распределения не имеют выбросов (переменная возраст заранее обработана от критических значений, индекс финансовой грамотности выбросов не имеет)
4. Условия, связанные с ошибками точек будут рассмотрены позже, после построения модели регрессии

In [11]:
dependency_data = pd.DataFrame()

dependency_data["Возраст"] = data["Age"]
dependency_data["Финансовая грамотность (%)"] = coeffs["Financial level %"]

dependency_data

Финансовая грамотность (%)  Возраст
0                              57       54
1                              43       47
2                              29       32
3                              86       25
4                              29       65
...                           ...      ...
12157                          86       42
12158                          71       44
12159                          57       18
12160                          43       67
12161                          86       44

[12162 rows x 2 columns]

In [13]:
dependency_data["Финансовая грамотность (%)"] = coeffs["Financial level %"]
dependency_data["Возраст"] = data["Age"]
dependency_data["Образование"] = data["Education"]
dependency_data["Family"] = data["Relationship"]
dependency_data["Возрастная группа"] = data["Age group"]
dependency_data["Gender"] = data["Gender"]
dependency_data["Living place"] = data["Type of residence"]

In [14]:
dependency_data = dependency_data[dependency_data["Возраст"] < 90]

2 и 3 условия о нормальности и выбросах

In [15]:
# УДАЛЕНИЕ ВЫБРОСОВ ЧЕРЕЗ IQR
def find_outliers_IQR(df):
   q1 = df.quantile(0.25)

   q3 = df.quantile(0.75)

   IQR = q3-q1

   outliers = df[((df < (q1 - 1.5 * IQR)) | (df > ( q3 + 1.5 * IQR)))]

   return outliers

In [16]:
# ГРАФИК РАСПРЕДЕЛЕНИЯ ВОЗРАСТА

fig = px.histogram(dependency_data["Возраст"], color_discrete_sequence = [colors[9]])

fig.update_yaxes(title = "Частота", title_font = dict(size = 18, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Значение", title_font = dict(size = 18, family = 'Arial', color = 'black'))

fig.update_layout(title = "Распределение возраста респондентов",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 30)

fig.update_layout(margin=dict(t = 90))

fig.update_yaxes(title_text='',row = 2, col = 1)
fig.update_xaxes(title_text='',row = 2, col = 1)

fig.update_layout(showlegend = False)
fig.update_layout(height = 600, width = 1200)

fig.show()

In [17]:
print(f"Выбросы, обнаруженные с помощью IQR: {find_outliers_IQR(dependency_data['Возраст']).values}")

Выбросы, обнаруженные с помощью IQR: []


In [18]:
X_age = dependency_data['Возраст']

In [19]:
# ГРАФИК РАСПРЕДЕЛЕНИЯ ИНДЕКСА ФИНАНСОВОЙ ГРАМОТНОСТИ

fig = px.histogram(dependency_data["Финансовая грамотность (%)"], nbins = 10, marginal = "box", color_discrete_sequence = ['rgb(42, 86, 116)'])

fig.update_yaxes(title = "Частота", title_font = dict(size = 18, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Значение, %", title_font = dict(size = 18, family = 'Arial', color = 'black'))

fig.update_layout(title = "Распределение значений финансовой грамотности респондентов",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 30)

fig.update_layout(margin=dict(t = 90))

fig.update_layout(
    xaxis = dict(
        tickmode = 'array',
        tickvals = [0, 20, 40, 60, 80, 99, 119],
        ticktext = [0, 20, 40, 60, 80, 99, 100]))


fig.update_yaxes(title_text='',row = 2, col = 1)
fig.update_xaxes(title_text='',row = 2, col = 1)

fig.update_layout(showlegend = False)
fig.update_layout(height = 600, width = 1200)

fig.show()

In [20]:
print(f"Выбросы, обнаруженные с помощью IQR: {find_outliers_IQR(dependency_data['Финансовая грамотность (%)']).values}")

Выбросы, обнаруженные с помощью IQR: [0 0 0 0 0 0 0 0 0 0 0 0 0]


In [21]:
dependency_data = dependency_data[dependency_data["Финансовая грамотность (%)"] > 0]
dependency_data

Финансовая грамотность (%)  Возраст               Образование  \
0                              57       54       Среднее специальное   
1                              43       47      Среднее общее и ниже   
2                              29       32      Среднее общее и ниже   
3                              86       25       Среднее специальное   
4                              29       65  Высшее и неполное высшее   
...                           ...      ...                       ...   
12157                          86       42      Среднее общее и ниже   
12158                          71       44      Среднее общее и ниже   
12159                          57       18      Среднее общее и ниже   
12160                          43       67      Среднее общее и ниже   
12161                          86       44  Высшее и неполное высшее   

                                                 Family Возрастная группа  \
0                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ         46-55 лет   
1                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ         46-55 лет   
2                                           РАЗВЕДЕН(А)         26-35 лет   
3      НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)         18-25 лет   
4                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   56 лет и старше   
...                                                 ...               ...   
12157                                       РАЗВЕДЕН(А)         36-45 лет   
12158                                       РАЗВЕДЕН(А)         36-45 лет   
12159  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)         18-25 лет   
12160                                      ВДОВЕЦ/ВДОВА   56 лет и старше   
12161                                       РАЗВЕДЕН(А)         36-45 лет   

        Gender Living place  
0      ЖЕНСКИЙ        Город  
1      МУЖСКОЙ        Город  
2      МУЖСКОЙ        Город  
3      МУЖСКОЙ        Город  
4      ЖЕНСКИЙ        Город  
...        ...          ...  
12157  МУЖСКОЙ        Город  
12158  ЖЕНСКИЙ        Город  
12159  ЖЕНСКИЙ        Город  
12160  ЖЕНСКИЙ        Город  
12161  ЖЕНСКИЙ        Город  

[12099 rows x 7 columns]

**Построение модели линейной регрессии**

In [24]:
dependency_data

Финансовая грамотность (%)  Возраст               Образование  \
0                              57       54       Среднее специальное   
1                              43       47      Среднее общее и ниже   
2                              29       32      Среднее общее и ниже   
3                              86       25       Среднее специальное   
4                              29       65  Высшее и неполное высшее   
...                           ...      ...                       ...   
12157                          86       42      Среднее общее и ниже   
12158                          71       44      Среднее общее и ниже   
12159                          57       18      Среднее общее и ниже   
12160                          43       67      Среднее общее и ниже   
12161                          86       44  Высшее и неполное высшее   

                                                 Family Возрастная группа  \
0                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ         46-55 лет   
1                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ         46-55 лет   
2                                           РАЗВЕДЕН(А)         26-35 лет   
3      НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)         18-25 лет   
4                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   56 лет и старше   
...                                                 ...               ...   
12157                                       РАЗВЕДЕН(А)         36-45 лет   
12158                                       РАЗВЕДЕН(А)         36-45 лет   
12159  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)         18-25 лет   
12160                                      ВДОВЕЦ/ВДОВА   56 лет и старше   
12161                                       РАЗВЕДЕН(А)         36-45 лет   

        Gender Living place  
0      ЖЕНСКИЙ        Город  
1      МУЖСКОЙ        Город  
2      МУЖСКОЙ        Город  
3      МУЖСКОЙ        Город  
4      ЖЕНСКИЙ        Город  
...        ...          ...  
12157  МУЖСКОЙ        Город  
12158  ЖЕНСКИЙ        Город  
12159  ЖЕНСКИЙ        Город  
12160  ЖЕНСКИЙ        Город  
12161  ЖЕНСКИЙ        Город  

[12099 rows x 7 columns]

In [71]:
import statsmodels.formula.api as smf

fingram = pd.DataFrame()
fingram["Education"] = dependency_data["Education"]
fingram["Age"] = dependency_data["Age"]
fingram["Age group"] = dependency_data["Age_group"]
fingram["Fingram"] = dependency_data["Fingram"]
fingram["Gender"]  = dependency_data["Gender"]
fingram["Income"] = dependency_data["Preproccesed_Income"]
fingram["Family"] = dependency_data["Family"]
fingram["Place_of_living"] = dependency_data["Place_of_living"]
#fingram["Family"] = dependency_data["Family"]
#fingram["Living_place"] = dependency_data["Living place"]

fingram = fingram[(fingram["Education"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ") & (fingram["Education"] != "НЕТ ОТВЕТА") & (fingram["Education"] != "ОТКАЗ ОТ ОТВЕТА")]
fingram = fingram[(fingram["Family"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ") & (fingram["Family"] != "НЕТ ОТВЕТА") & (fingram["Family"] != "ОТКАЗ ОТ ОТВЕТА")]

In [72]:
fingram

Education  Age        Age group  Fingram   Gender  \
0           Среднее специальное   54        46-55 лет       57  ЖЕНСКИЙ   
1          Среднее общее и ниже   47        46-55 лет       43  МУЖСКОЙ   
2          Среднее общее и ниже   32        26-35 лет       29  МУЖСКОЙ   
3           Среднее специальное   25        18-25 лет       86  МУЖСКОЙ   
4      Высшее и неполное высшее   65  56 лет и старше       29  ЖЕНСКИЙ   
...                         ...  ...              ...      ...      ...   
12157      Среднее общее и ниже   42        36-45 лет       86  МУЖСКОЙ   
12158      Среднее общее и ниже   44        36-45 лет       71  ЖЕНСКИЙ   
12159      Среднее общее и ниже   18        18-25 лет       57  ЖЕНСКИЙ   
12160      Среднее общее и ниже   67  56 лет и старше       43  ЖЕНСКИЙ   
12161  Высшее и неполное высшее   44        36-45 лет       86  ЖЕНСКИЙ   

       Income                                            Family  \
0       50000                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
1       50000                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
2       90000                                       РАЗВЕДЕН(А)   
3       18000  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
4       26900                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
...       ...                                               ...   
12157   30000                                       РАЗВЕДЕН(А)   
12158   20000                                       РАЗВЕДЕН(А)   
12159   32000  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
12160   23800                                      ВДОВЕЦ/ВДОВА   
12161   58000                                       РАЗВЕДЕН(А)   

      Place_of_living  
0               Город  
1               Город  
2               Город  
3               Город  
4               Город  
...               ...  
12157           Город  
12158           Город  
12159           Город  
12160           Город  
12161           Город  

[11766 rows x 8 columns]

In [73]:
education_map = {'Среднее общее и ниже': 1, 'Высшее и неполное высшее': 2, "Среднее специальное" : 3}
gender_map = {"ЖЕНСКИЙ" : 1, "МУЖСКОЙ" : 2}

In [74]:
fingram["Family"] = fingram["Family"].map(family_map)
fingram["Place_of_living"] = fingram["Place_of_living"].map(place_map)
fingram["Education"] = fingram["Education"].map(education_map)
fingram["Gender"] = fingram["Gender"].map(gender_map)

fingram

Education  Age        Age group  Fingram  Gender  Income  Family  \
0              3   54        46-55 лет       57       1   50000       1   
1              1   47        46-55 лет       43       2   50000       1   
2              1   32        26-35 лет       29       2   90000       2   
3              3   25        18-25 лет       86       2   18000       3   
4              2   65  56 лет и старше       29       1   26900       1   
...          ...  ...              ...      ...     ...     ...     ...   
12157          1   42        36-45 лет       86       2   30000       2   
12158          1   44        36-45 лет       71       1   20000       2   
12159          1   18        18-25 лет       57       1   32000       3   
12160          1   67  56 лет и старше       43       1   23800       4   
12161          2   44        36-45 лет       86       1   58000       2   

       Place_of_living  
0                    1  
1                    1  
2                    1  
3                    1  
4                    1  
...                ...  
12157                1  
12158                1  
12159                1  
12160                1  
12161                1  

[11766 rows x 8 columns]

In [60]:
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

weights = np.polyfit(fingram["Age"], fingram["Fingram"], 2)
model = np.poly1d(weights)
results = smf.ols(formula='Fingram ~ model(Age) + Income', data = fingram).fit() # ДОБАВЛЕНИЕ ФАКТОРА

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.035
Model:                            OLS   Adj. R-squared:                  0.035
Method:                 Least Squares   F-statistic:                     212.9
Date:                Mon, 18 Dec 2023   Prob (F-statistic):           1.45e-91
Time:                        20:41:58   Log-Likelihood:                -54021.
No. Observations:               11766   AIC:                         1.080e+05
Df Residuals:                   11763   BIC:                         1.081e+05
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept      7.7192      4.674      1.652      0.099      -1.442      16.880
model(Age)     0.8337      0.071     11.803      0.000       0.695       0.972
Income         0.0001    7.6e-06     14.841      0.000     9.8e-05       0.000
==============================================================================
Omnibus:                      586.132   Durbin-Watson:                   1.987
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              465.704
Skew:                          -0.403   Prob(JB):                    7.48e-102
Kurtosis:                       2.453   Cond. No.                     8.85e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 8.85e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [75]:
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

weights = np.polyfit(fingram["Age"], fingram["Fingram"], 2)
model = np.poly1d(weights)
results = smf.ols(formula='Fingram ~ model(Age) + Income + Education + Family + Place_of_living + Gender', data = fingram).fit() # ДОБАВЛЕНИЕ ФАКТОРА

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.106
Model:                            OLS   Adj. R-squared:                  0.105
Method:                 Least Squares   F-statistic:                     231.9
Date:                Mon, 18 Dec 2023   Prob (F-statistic):          5.14e-281
Time:                        20:48:30   Log-Likelihood:                -53572.
No. Observations:               11766   AIC:                         1.072e+05
Df Residuals:                   11759   BIC:                         1.072e+05
Df Model:                           6                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
Intercept          25.6058      4.942      5.182      0.000      15.920      35.292
model(Age)          0.7471      0.071     10.467      0.000       0.607       0.887
Income           8.155e-05   7.48e-06     10.906      0.000    6.69e-05    9.62e-05
Education           3.9837      0.262     15.196      0.000       3.470       4.498
Family             -1.0652      0.202     -5.273      0.000      -1.461      -0.669
Place_of_living   -11.7713      0.487    -24.191      0.000     -12.725     -10.817
Gender             -0.9868      0.444     -2.222      0.026      -1.857      -0.116
==============================================================================
Omnibus:                      480.243   Durbin-Watson:                   1.993
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              434.681
Skew:                          -0.413   Prob(JB):                     4.08e-95
Kurtosis:                       2.549   Cond. No.                     9.73e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 9.73e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [193]:
weights

array([-7.94872642e-03,  6.84200284e-01,  5.45374762e+01])

In [80]:
import statsmodels.formula.api as smf

fingram = pd.DataFrame()
fingram["Education"] = dependency_data["Образование"]
fingram["Age"] = dependency_data["Возраст"]
fingram["Fingram"] = dependency_data["Финансовая грамотность (%)"]
fingram["Family"] = dependency_data["Family"]
fingram["Living_place"] = dependency_data["Living place"]

fingram = fingram[(fingram["Education"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ") & (fingram["Education"] != "НЕТ ОТВЕТА") & (fingram["Education"] != "ОТКАЗ ОТ ОТВЕТА")]
fingram = fingram[(fingram["Family"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ") & (fingram["Family"] != "НЕТ ОТВЕТА") & (fingram["Family"] != "ОТКАЗ ОТ ОТВЕТА")]

fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

lin_model = smf.ols("Age ~ Fingram + Education + Family + Living_place", data = fingram).fit()

lin_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                    Age   R-squared:                       0.405
Model:                            OLS   Adj. R-squared:                  0.405
Method:                 Least Squares   F-statistic:                     1170.
Date:                Sun, 17 Dec 2023   Prob (F-statistic):               0.00
Time:                        17:48:46   Log-Likelihood:                -48137.
No. Observations:               12027   AIC:                         9.629e+04
Df Residuals:                   12019   BIC:                         9.635e+04
Df Model:                           7                                         
Covariance Type:            nonrobust                                         
==============================================================================================================================
                                                                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------------------------------------------------------
Intercept                                                     68.6939      0.565    121.617      0.000      67.587      69.801
Education[T.Среднее общее и ниже]                              2.1599      0.306      7.054      0.000       1.560       2.760
Education[T.Среднее специальное]                               2.2931      0.334      6.863      0.000       1.638       2.948
Family[T.НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)]   -36.4679      0.425    -85.716      0.000     -37.302     -35.634
Family[T.РАЗВЕДЕН(А)]                                        -16.3326      0.474    -34.488      0.000     -17.261     -15.404
Family[T.СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ]                  -17.1437      0.379    -45.177      0.000     -17.888     -16.400
Living_place[T.Село]                                           0.1517      0.284      0.535      0.593      -0.404       0.708
Fingram                                                       -0.0276      0.005     -5.166      0.000      -0.038      -0.017
==============================================================================
Omnibus:                      192.223   Durbin-Watson:                   0.771
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              199.261
Skew:                           0.308   Prob(JB):                     5.38e-44
Kurtosis:                       2.867   Cond. No.                         445.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [78]:
dependency_data["Living place"].unique()

array(['Город', 'Село'], dtype=object)

In [83]:
import statsmodels.formula.api as smf

fingram = pd.DataFrame()
fingram["Education"] = dependency_data["Образование"]
fingram["Age"] = dependency_data["Возраст"]
fingram["Fingram"] = dependency_data["Финансовая грамотность (%)"]
fingram["Family"] = dependency_data["Family"]
fingram["Living_place"] = dependency_data["Living place"].map({"Село" : 1, "Город" : 2})

fingram = fingram[(fingram["Education"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ") & (fingram["Education"] != "НЕТ ОТВЕТА") & (fingram["Education"] != "ОТКАЗ ОТ ОТВЕТА")]
fingram = fingram[(fingram["Family"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ") & (fingram["Family"] != "НЕТ ОТВЕТА") & (fingram["Family"] != "ОТКАЗ ОТ ОТВЕТА")]

fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

lin_model = smf.ols("Fingram ~ Education + Living_place + Family + Age + Age:Living_place + Education:Age", data = fingram).fit()

lin_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.141
Model:                            OLS   Adj. R-squared:                  0.140
Method:                 Least Squares   F-statistic:                     197.1
Date:                Sun, 17 Dec 2023   Prob (F-statistic):               0.00
Time:                        17:51:45   Log-Likelihood:                -54519.
No. Observations:               12027   AIC:                         1.091e+05
Df Residuals:                   12016   BIC:                         1.091e+05
Df Model:                          10                                         
Covariance Type:            nonrobust                                         
==============================================================================================================================
                                                                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------------------------------------------------------
Intercept                                                     52.0239      3.164     16.440      0.000      45.821      58.227
Education[T.Среднее общее и ниже]                             -8.9288      1.518     -5.881      0.000     -11.905      -5.953
Education[T.Среднее специальное]                             -10.0087      1.784     -5.611      0.000     -13.505      -6.512
Family[T.НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)]     1.1884      0.921      1.290      0.197      -0.618       2.994
Family[T.РАЗВЕДЕН(А)]                                          2.0702      0.845      2.449      0.014       0.414       3.727
Family[T.СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ]                    4.6396      0.697      6.658      0.000       3.274       6.006
Living_place                                                  12.6776      1.486      8.532      0.000       9.765      15.590
Age                                                            0.0568      0.058      0.973      0.331      -0.058       0.171
Education[T.Среднее общее и ниже]:Age                         -0.1352      0.030     -4.528      0.000      -0.194      -0.077
Education[T.Среднее специальное]:Age                           0.0249      0.034      0.724      0.469      -0.043       0.092
Age:Living_place                                              -0.0446      0.028     -1.578      0.115      -0.100       0.011
==============================================================================
Omnibus:                      429.425   Durbin-Watson:                   1.978
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              409.515
Skew:                          -0.407   Prob(JB):                     1.19e-89
Kurtosis:                       2.608   Cond. No.                     1.90e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.9e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [164]:
fingram = fingram.sort_values(by = "Age", ascending = True)
lin_predict = results.predict(fingram[["Age", "Education", "Gender", "Income"]])

fig = go.Figure()

fig = px.scatter(x = fingram["Age"], y = fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = fingram["Age"], y = lin_predict, name = "Линейная регрессия", ))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Прямая линейной регрессии (R-squared = {round(lin_model.rsquared, 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [121]:
model

poly1d([-8.04014977e-03,  6.94203625e-01,  5.41974261e+01])

In [77]:
fingram

index  Education  Age        Age group  Fingram  Gender  Income  \
0      10038          3   18        18-25 лет       43       2   11000   
1       6651          1   18        18-25 лет       86       2     930   
2      10249          2   18        18-25 лет       86       1       0   
3       7269          1   18        18-25 лет       86       1       0   
4      10126          1   18        18-25 лет       14       1       0   
...      ...        ...  ...              ...      ...     ...     ...   
11761   8768          1   89  56 лет и старше       43       1   20000   
11762   5594          2   89  56 лет и старше       57       1   36400   
11763   5481          1   89  56 лет и старше       14       2   19000   
11764   9649          3   89  56 лет и старше       71       1   25881   
11765   2666          1   89  56 лет и старше       29       1   26000   

       Family  Place_of_living  
0           3                2  
1           3                1  
2           3                1  
3           3                2  
4           3                2  
...       ...              ...  
11761       4                1  
11762       4                2  
11763       4                2  
11764       4                1  
11765       4                2  

[11766 rows x 9 columns]

In [79]:
results = smf.ols("Fingram ~ Age + Income + Education + Family + Place_of_living + Gender", data = fingram).fit()

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.102
Model:                            OLS   Adj. R-squared:                  0.102
Method:                 Least Squares   F-statistic:                     223.4
Date:                Mon, 18 Dec 2023   Prob (F-statistic):          4.06e-271
Time:                        20:59:25   Log-Likelihood:                -53595.
No. Observations:               11766   AIC:                         1.072e+05
Df Residuals:                   11759   BIC:                         1.073e+05
Df Model:                           6                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
Intercept          81.1216      1.388     58.431      0.000      78.400      83.843
Age                -0.0991      0.012     -7.970      0.000      -0.123      -0.075
Income           8.844e-05   7.44e-06     11.887      0.000    7.39e-05       0.000
Education           4.0816      0.263     15.544      0.000       3.567       4.596
Family             -1.6988      0.194     -8.773      0.000      -2.078      -1.319
Place_of_living   -11.5372      0.488    -23.660      0.000     -12.493     -10.581
Gender             -1.2331      0.447     -2.757      0.006      -2.110      -0.356
==============================================================================
Omnibus:                      487.664   Durbin-Watson:                   1.988
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              443.065
Skew:                          -0.418   Prob(JB):                     6.16e-97
Kurtosis:                       2.548   Cond. No.                     2.83e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 2.83e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [83]:
fingram = fingram.sort_values(by = "Age", ascending = True)
lin_predict = results.predict(fingram[["Age", "Education", "Gender", "Income", "Family", "Place_of_living"]])

fig = go.Figure()

fig = px.scatter(x = fingram["Age"], y = fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = fingram["Age"], y = lin_predict, name = "Линейная регрессия", ))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Прямая линейной регрессии",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [146]:
mean_financial = []


for age in dependency_data["Возраст"].unique():
    mean_financial.append(np.round(np.mean(dependency_data["Финансовая грамотность (%)"][dependency_data["Возраст"] == age])))

mean_fingram = pd.DataFrame()
mean_fingram["Fingram"] = mean_financial
mean_fingram["Age"] = dependency_data["Возраст"].unique()

mean_fingram

Fingram  Age
0      70.0   54
1      68.0   47
2      70.0   32
3      65.0   25
4      66.0   65
..      ...  ...
67     59.0   82
68     44.0   87
69     55.0   88
70     51.0   83
71     66.0   78

[72 rows x 2 columns]

In [147]:
mean_fingram = mean_fingram.sort_values(by = "Age", ascending = True).reset_index()
mean_fingram

index  Fingram  Age
0      15     61.0   18
1      14     60.0   19
2      55     62.0   20
3      21     64.0   21
4      50     62.0   22
..    ...      ...  ...
67     27     51.0   85
68     58     53.0   86
69     68     44.0   87
70     69     55.0   88
71     62     46.0   89

[72 rows x 3 columns]

In [148]:
lin_model = smf.ols("Fingram ~ Age", data = mean_fingram).fit()

lin_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.382
Model:                            OLS   Adj. R-squared:                  0.373
Method:                 Least Squares   F-statistic:                     43.27
Date:                Sun, 17 Dec 2023   Prob (F-statistic):           7.29e-09
Time:                        20:01:47   Log-Likelihood:                -213.40
No. Observations:                  72   AIC:                             430.8
Df Residuals:                      70   BIC:                             435.3
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     74.2231      1.547     47.969      0.000      71.137      77.309
Age           -0.1773      0.027     -6.578      0.000      -0.231      -0.124
==============================================================================
Omnibus:                       17.173   Durbin-Watson:                   0.683
Prob(Omnibus):                  0.000   Jarque-Bera (JB):               20.196
Skew:                          -1.225   Prob(JB):                     4.12e-05
Kurtosis:                       3.853   Cond. No.                         159.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [129]:
lin_predict = lin_model.predict(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = lin_predict, name = "Линейная регрессия", ))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Прямая линейной регрессии (R-squared = {round(lin_model.rsquared, 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [150]:
model_poly = np.poly1d(np.polyfit(mean_fingram["Age"], mean_fingram["Fingram"], 2))

In [151]:
from sklearn.metrics import r2_score

poly_predict = model_poly(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Кривая полиномиальной регрессии (R-squared = {round(r2_score(mean_fingram['Fingram'], model_poly(mean_fingram['Age'])), 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [152]:
poly_predict = model_poly(mean_fingram["Age"])
lin_predict = lin_model.predict(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=["#74777B"]) #colors[9]
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия", marker_color = "#0088BB"))
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = lin_predict, name = "Линейная регрессия", marker_color = "#EE1133"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = "Сравнение полиномиальной и линейной регрессий",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

РЕГРЕССИОННЫЙ АНАЛИЗ ДЛЯ ПОДВЫБОРОК ПО УРОВНЮ ОБРАЗОВАНИЯ

In [23]:
dependency_data

Финансовая грамотность (%)  Возраст               Образование
0                              57       54       Среднее специальное
1                              43       47      Среднее общее и ниже
2                              29       32      Среднее общее и ниже
3                              86       25       Среднее специальное
4                              29       65  Высшее и неполное высшее
...                           ...      ...                       ...
12157                          86       42      Среднее общее и ниже
12158                          71       44      Среднее общее и ниже
12159                          57       18      Среднее общее и ниже
12160                          43       67      Среднее общее и ниже
12161                          86       44  Высшее и неполное высшее

[12099 rows x 3 columns]

In [27]:
dependency_data = dependency_data.rename(mapper = {"Финансовая грамотность (%)" : "Fingram",
                                                   "Возраст" : "Age",
                                                   "Возрастная группа" : "Age_group",
                                                   "Образование" : "Education"}, axis = 1)
dependency_data

Fingram  Age                 Education  \
0           57   54       Среднее специальное   
1           43   47      Среднее общее и ниже   
2           29   32      Среднее общее и ниже   
3           86   25       Среднее специальное   
4           29   65  Высшее и неполное высшее   
...        ...  ...                       ...   
12157       86   42      Среднее общее и ниже   
12158       71   44      Среднее общее и ниже   
12159       57   18      Среднее общее и ниже   
12160       43   67      Среднее общее и ниже   
12161       86   44  Высшее и неполное высшее   

                                                 Family        Age_group  \
0                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ        46-55 лет   
1                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ        46-55 лет   
2                                           РАЗВЕДЕН(А)        26-35 лет   
3      НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)        18-25 лет   
4                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ  56 лет и старше   
...                                                 ...              ...   
12157                                       РАЗВЕДЕН(А)        36-45 лет   
12158                                       РАЗВЕДЕН(А)        36-45 лет   
12159  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)        18-25 лет   
12160                                      ВДОВЕЦ/ВДОВА  56 лет и старше   
12161                                       РАЗВЕДЕН(А)        36-45 лет   

        Gender Living place  
0      ЖЕНСКИЙ        Город  
1      МУЖСКОЙ        Город  
2      МУЖСКОЙ        Город  
3      МУЖСКОЙ        Город  
4      ЖЕНСКИЙ        Город  
...        ...          ...  
12157  МУЖСКОЙ        Город  
12158  ЖЕНСКИЙ        Город  
12159  ЖЕНСКИЙ        Город  
12160  ЖЕНСКИЙ        Город  
12161  ЖЕНСКИЙ        Город  

[12099 rows x 7 columns]

In [34]:
dependency_data_school = dependency_data[dependency_data["Education"] == "Среднее общее и ниже"]
dependency_data_middle = dependency_data[dependency_data["Education"] == "Среднее специальное"]
dependency_data_high = dependency_data[dependency_data["Education"] == "Высшее и неполное высшее"]

**СРЕДНЕЕ ОБЩЕЕ И НИЖЕ**

In [35]:
mean_financial_school = []

for age in dependency_data_school["Age"].unique():
    mean_financial_school.append(np.round(np.mean(dependency_data_school["Fingram"][dependency_data_school["Age"] == age])))

mean_fingram_school = pd.DataFrame()
mean_fingram_school["Fingram"] = mean_financial_school
mean_fingram_school["Age"] = dependency_data_school["Age"].unique()

mean_fingram_school

Fingram  Age
0      59.0   47
1      62.0   32
2      60.0   19
3      61.0   18
4      60.0   59
..      ...  ...
67     55.0   79
68     51.0   78
69     38.0   87
70     61.0   24
71     63.0   23

[72 rows x 2 columns]

In [36]:
mean_fingram_school = mean_fingram_school.sort_values(by = "Age", ascending = True).reset_index()
mean_fingram_school

index  Fingram  Age
0       3     61.0   18
1       2     60.0   19
2      45     64.0   20
3      40     63.0   21
4      48     64.0   22
..    ...      ...  ...
67     58     37.0   85
68     37     42.0   86
69     69     38.0   87
70     62     46.0   88
71     41     38.0   89

[72 rows x 3 columns]

In [37]:
# СРЕДНЕЕ ОБЩЕЕ И НИЖЕ

lin_model = smf.ols("Fingram ~ Age", data = mean_fingram_school).fit()
model_poly = np.poly1d(np.polyfit(mean_fingram_school["Age"], mean_fingram_school["Fingram"], 3))

poly_predict = model_poly(mean_fingram_school["Age"])
lin_predict = lin_model.predict(mean_fingram_school["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram_school["Age"], y = mean_fingram_school["Fingram"], color_discrete_sequence=["#74777B"]) #colors[9]
fig.add_trace(go.Scatter(x = mean_fingram_school["Age"], y = poly_predict, name = "Полиномиальная регрессия", marker_color = "#0088BB"))
fig.add_trace(go.Scatter(x = mean_fingram_school["Age"], y = lin_predict, name = "Линейная регрессия", marker_color = "#EE1133"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = "Сравнение полиномиальной и линейной регрессий<br><sup>Среднее общее образование и ниже",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [82]:
lin_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.552
Model:                            OLS   Adj. R-squared:                  0.546
Method:                 Least Squares   F-statistic:                     86.27
Date:                Sun, 17 Dec 2023   Prob (F-statistic):           7.86e-14
Time:                        14:24:27   Log-Likelihood:                -210.37
No. Observations:                  72   AIC:                             424.7
Df Residuals:                      70   BIC:                             429.3
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     70.6923      1.484     47.647      0.000      67.733      73.651
Age           -0.2401      0.026     -9.288      0.000      -0.292      -0.189
==============================================================================
Omnibus:                        9.094   Durbin-Watson:                   1.298
Prob(Omnibus):                  0.011   Jarque-Bera (JB):                8.947
Skew:                          -0.845   Prob(JB):                       0.0114
Kurtosis:                       3.358   Cond. No.                         159.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [83]:
from sklearn.metrics import r2_score

r2_score(mean_fingram_school["Fingram"], poly_predict)

0.7768756565703752

**СРЕДНЕЕ СПЕЦИАЛЬНОЕ**

In [53]:
mean_financial_middle = []

for age in dependency_data_middle["Age"].unique():
    mean_financial_middle.append(np.round(np.mean(dependency_data_middle["Fingram"][dependency_data_middle["Age"] == age])))

mean_fingram_middle = pd.DataFrame()
mean_fingram_middle["Fingram"] = mean_financial_middle
mean_fingram_middle["Age"] = dependency_data_middle["Age"].unique()

mean_fingram_middle

Fingram  Age
0      72.0   54
1      69.0   25
2      65.0   63
3      64.0   61
4      64.0   49
..      ...  ...
67     41.0   80
68     58.0   19
69     64.0   86
70     71.0   89
71     57.0   18

[72 rows x 2 columns]

In [54]:
# ГРАФИК РАСПРЕДЕЛЕНИЯ ИНДЕКСА ФИНАНСОВОЙ ГРАМОТНОСТИ

fig = px.histogram(mean_fingram_middle["Fingram"], nbins = 10, marginal = "box", color_discrete_sequence = ['rgb(42, 86, 116)'])

fig.update_yaxes(title = "Частота", title_font = dict(size = 18, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Значение, %", title_font = dict(size = 18, family = 'Arial', color = 'black'))

fig.update_layout(title = "Распределение значений финансовой грамотности респондентов, получивших среднее специальнле образование",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 30)

fig.update_layout(margin=dict(t = 90))

fig.update_layout(
    xaxis = dict(
        tickmode = 'array',
        tickvals = [0, 20, 40, 60, 80, 99, 119],
        ticktext = [0, 20, 40, 60, 80, 99, 100]))


fig.update_yaxes(title_text='',row = 2, col = 1)
fig.update_xaxes(title_text='',row = 2, col = 1)

fig.update_layout(showlegend = False)
fig.update_layout(height = 600, width = 1200)

fig.show()

In [55]:
mean_fingram_middle = mean_fingram_middle[mean_fingram_middle["Fingram"] > 44]

In [56]:
# СРЕДНЕЕ СПЕЦИАЛЬНОЕ
mean_fingram_middle = mean_fingram_middle.sort_values(by = "Age", ascending = True).reset_index()

lin_model = smf.ols("Fingram ~ Age", data = mean_fingram_middle).fit()
model_poly = np.poly1d(np.polyfit(mean_fingram_middle["Age"], mean_fingram_middle["Fingram"], 3))

poly_predict = model_poly(mean_fingram_middle["Age"])
lin_predict = lin_model.predict(mean_fingram_middle["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram_middle["Age"], y = mean_fingram_middle["Fingram"], color_discrete_sequence=["#74777B"]) #colors[9]
fig.add_trace(go.Scatter(x = mean_fingram_middle["Age"], y = poly_predict, name = "Полиномиальная регрессия", marker_color = "#0088BB"))
fig.add_trace(go.Scatter(x = mean_fingram_middle["Age"], y = lin_predict, name = "Линейная регрессия", marker_color = "#EE1133"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = "Сравнение полиномиальной и линейной регрессий<br><sup>Среднее специальное образование",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [57]:
lin_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.000
Model:                            OLS   Adj. R-squared:                 -0.014
Method:                 Least Squares   F-statistic:                   0.03130
Date:                Sun, 17 Dec 2023   Prob (F-statistic):              0.860
Time:                        17:02:20   Log-Likelihood:                -210.32
No. Observations:                  70   AIC:                             424.6
Df Residuals:                      68   BIC:                             429.1
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     66.2451      1.633     40.572      0.000      62.987      69.503
Age            0.0051      0.029      0.177      0.860      -0.053       0.063
==============================================================================
Omnibus:                        4.810   Durbin-Watson:                   1.516
Prob(Omnibus):                  0.090   Jarque-Bera (JB):                4.363
Skew:                          -0.610   Prob(JB):                        0.113
Kurtosis:                       3.076   Cond. No.                         156.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [58]:
from sklearn.metrics import r2_score

r2_score(mean_fingram_middle["Fingram"], poly_predict)

0.2796990898349492

**Высшее и неполное высшее**

In [44]:
mean_financial_high = []

for age in dependency_data_high["Age"].unique():
    mean_financial_high.append(np.round(np.mean(dependency_data_high["Fingram"][dependency_data_high["Age"] == age])))

mean_fingram_high = pd.DataFrame()
mean_fingram_high["Fingram"] = mean_financial_high
mean_fingram_high["Age"] = dependency_data_high["Age"].unique()

mean_fingram_high 

Fingram  Age
0      76.0   65
1      75.0   72
2      82.0   43
3      75.0   31
4      78.0   40
..      ...  ...
67     74.0   82
68     77.0   78
69     71.0   89
70     86.0   18
71     71.0   19

[72 rows x 2 columns]

In [48]:
# СРЕДНЕЕ СПЕЦИАЛЬНОЕ
mean_fingram_high= mean_fingram_high.sort_values(by = "Age", ascending = True).reset_index()

lin_model = smf.ols("Fingram ~ Age", data = mean_fingram_high).fit()
model_poly = np.poly1d(np.polyfit(mean_fingram_high["Age"], mean_fingram_high["Fingram"], 3))

poly_predict = model_poly(mean_fingram_high["Age"])
lin_predict = lin_model.predict(mean_fingram_high["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram_high["Age"], y = mean_fingram_high["Fingram"], color_discrete_sequence=["#74777B"]) #colors[9]
fig.add_trace(go.Scatter(x = mean_fingram_high["Age"], y = poly_predict, name = "Полиномиальная регрессия", marker_color = "#0088BB"))
fig.add_trace(go.Scatter(x = mean_fingram_high["Age"], y = lin_predict, name = "Линейная регрессия", marker_color = "#EE1133"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = "Сравнение полиномиальной и линейной регрессий<br><sup>Высшее и неполное высшее образование",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [49]:
lin_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.015
Model:                            OLS   Adj. R-squared:                  0.001
Method:                 Least Squares   F-statistic:                     1.095
Date:                Sun, 17 Dec 2023   Prob (F-statistic):              0.299
Time:                        16:54:56   Log-Likelihood:                -238.76
No. Observations:                  72   AIC:                             481.5
Df Residuals:                      70   BIC:                             486.1
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     78.0489      2.201     35.466      0.000      73.660      82.438
Age           -0.0401      0.038     -1.046      0.299      -0.117       0.036
==============================================================================
Omnibus:                       37.315   Durbin-Watson:                   1.583
Prob(Omnibus):                  0.000   Jarque-Bera (JB):               89.458
Skew:                          -1.742   Prob(JB):                     3.75e-20
Kurtosis:                       7.205   Cond. No.                         159.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [47]:
from sklearn.metrics import r2_score

r2_score(mean_fingram_high["Fingram"], poly_predict)

0.20955987913800334

**ВСТРЕЧА С МЕНТОРАМИ -> ПЕРЕХОД НА НОВУЮ МАТ МОДЕЛЬ ЧЕРЕЗ РЕГРЕССИИ**

1. Сложный вариант:
    * Проведение регрессионного анализа и построение графика получившихся функций
    * Выбор одной из регрессионных моделей -> полиномиальная регрессия
    * Обоснование выбора и обоснование выбора порядка модели
    * Добавление контрольного фактора в виде переменной "Образования"
    * Обьяснение получившейся формулы регрессионной модели (почему график таков, пик фин. грамотности, и т.д)
2. Простой вариант:
    * Построение прямых линейной регрессии для возрастных групп, которые создают видимость нелинейной свзяи между переменными

Средний индекс финансовой грамотности для каждого из возрастов в виде целевой переменной используется во многих исследованиях (например, https://sci-hub.hkvisa.net/10.2139/ssrn.1948627), что позволяет использовать именно такой подход.

In [113]:
dependency_data = pd.DataFrame()

dependency_data["Fingram"] = coeffs["Financial level %"]
dependency_data["Age"] = data["Age"]
dependency_data["Gender"] = data["Gender"]
dependency_data["Age_group"] = data["Age group"]
dependency_data["Education"] = data["Education"]
dependency_data["Place_of_living"] = data["Type of residence"]
dependency_data["Income"] = data_archive["k66a"]

dependency_data

Fingram  Age   Gender        Age_group                 Education  \
0           57   54  ЖЕНСКИЙ        46-55 лет       Среднее специальное   
1           43   47  МУЖСКОЙ        46-55 лет      Среднее общее и ниже   
2           29   32  МУЖСКОЙ        26-35 лет      Среднее общее и ниже   
3           86   25  МУЖСКОЙ        18-25 лет       Среднее специальное   
4           29   65  ЖЕНСКИЙ  56 лет и старше  Высшее и неполное высшее   
...        ...  ...      ...              ...                       ...   
12157       86   42  МУЖСКОЙ        36-45 лет      Среднее общее и ниже   
12158       71   44  ЖЕНСКИЙ        36-45 лет      Среднее общее и ниже   
12159       57   18  ЖЕНСКИЙ        18-25 лет      Среднее общее и ниже   
12160       43   67  ЖЕНСКИЙ  56 лет и старше      Среднее общее и ниже   
12161       86   44  ЖЕНСКИЙ        36-45 лет  Высшее и неполное высшее   

      Place_of_living Income  
0               Город  50000  
1               Город  50000  
2               Город  90000  
3               Город  18000  
4               Город  26900  
...               ...    ...  
12157           Город  30000  
12158           Город  20000  
12159           Город  32000  
12160           Город  23800  
12161           Город  58000  

[12162 rows x 7 columns]

In [114]:
dependency_data = dependency_data.dropna()
dependency_data

Fingram  Age   Gender        Age_group                 Education  \
0           57   54  ЖЕНСКИЙ        46-55 лет       Среднее специальное   
1           43   47  МУЖСКОЙ        46-55 лет      Среднее общее и ниже   
2           29   32  МУЖСКОЙ        26-35 лет      Среднее общее и ниже   
3           86   25  МУЖСКОЙ        18-25 лет       Среднее специальное   
4           29   65  ЖЕНСКИЙ  56 лет и старше  Высшее и неполное высшее   
...        ...  ...      ...              ...                       ...   
12157       86   42  МУЖСКОЙ        36-45 лет      Среднее общее и ниже   
12158       71   44  ЖЕНСКИЙ        36-45 лет      Среднее общее и ниже   
12159       57   18  ЖЕНСКИЙ        18-25 лет      Среднее общее и ниже   
12160       43   67  ЖЕНСКИЙ  56 лет и старше      Среднее общее и ниже   
12161       86   44  ЖЕНСКИЙ        36-45 лет  Высшее и неполное высшее   

      Place_of_living Income  
0               Город  50000  
1               Город  50000  
2               Город  90000  
3               Город  18000  
4               Город  26900  
...               ...    ...  
12157           Город  30000  
12158           Город  20000  
12159           Город  32000  
12160           Город  23800  
12161           Город  58000  

[11877 rows x 7 columns]

In [115]:
plus_90 = dependency_data[dependency_data["Age"] >= 90]
dependency_data = dependency_data[dependency_data["Age"] < 90]
dependency_data

Fingram  Age   Gender        Age_group                 Education  \
0           57   54  ЖЕНСКИЙ        46-55 лет       Среднее специальное   
1           43   47  МУЖСКОЙ        46-55 лет      Среднее общее и ниже   
2           29   32  МУЖСКОЙ        26-35 лет      Среднее общее и ниже   
3           86   25  МУЖСКОЙ        18-25 лет       Среднее специальное   
4           29   65  ЖЕНСКИЙ  56 лет и старше  Высшее и неполное высшее   
...        ...  ...      ...              ...                       ...   
12157       86   42  МУЖСКОЙ        36-45 лет      Среднее общее и ниже   
12158       71   44  ЖЕНСКИЙ        36-45 лет      Среднее общее и ниже   
12159       57   18  ЖЕНСКИЙ        18-25 лет      Среднее общее и ниже   
12160       43   67  ЖЕНСКИЙ  56 лет и старше      Среднее общее и ниже   
12161       86   44  ЖЕНСКИЙ        36-45 лет  Высшее и неполное высшее   

      Place_of_living Income  
0               Город  50000  
1               Город  50000  
2               Город  90000  
3               Город  18000  
4               Город  26900  
...               ...    ...  
12157           Город  30000  
12158           Город  20000  
12159           Город  32000  
12160           Город  23800  
12161           Город  58000  

[11828 rows x 7 columns]

In [119]:
fig = px.histogram(plus_90["Age"], color_discrete_sequence = ['#0088BB'])

fig.update_yaxes(title = "Частота", title_font = dict(size = 18, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Значение, %", title_font = dict(size = 18, family = 'Arial', color = 'black'))

fig.update_layout(showlegend = False)
fig.update_layout(height = 800, width = 1000)

fig.show()

**Порядок модели**

In [126]:
model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 2)
model_poly

(-1.5070422535211268, 0.028169014084507043)

In [127]:
model_poly

Polynomial([ 68.87865991,  -6.27568493, -11.84401225], domain=[18., 89.], window=[-1.,  1.])

In [97]:
# ВТОРОЙ ПОРЯДОК

fingram = dependency_data[["Age", "Fingram"]]
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

mean_fingram = pd.DataFrame()
mean_fingram_level = []

for age in fingram["Age"].unique():
    mean_fingram_level.append(np.round(np.mean(fingram["Fingram"][fingram["Age"] == age])))

mean_fingram["Fingram"] = mean_fingram_level
mean_fingram["Age"] = fingram["Age"].unique()

model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 2)

from sklearn.metrics import r2_score

poly_predict = model_poly(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия второго порядка<br><sup>(R-squared = {round(r2_score(mean_fingram['Fingram'], model_poly(mean_fingram['Age'])), 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [98]:
model_poly

Polynomial([ 68.87865991,  -6.27568493, -11.84401225], domain=[18., 89.], window=[-1.,  1.])

In [99]:
# ТРЕТИЙ ПОРЯДОК

fingram = dependency_data[["Age", "Fingram"]]
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

mean_fingram = pd.DataFrame()
mean_fingram_level = []

for age in fingram["Age"].unique():
    mean_fingram_level.append(np.round(np.mean(fingram["Fingram"][fingram["Age"] == age])))

mean_fingram["Fingram"] = mean_fingram_level
mean_fingram["Age"] = fingram["Age"].unique()

model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 3)

from sklearn.metrics import r2_score

poly_predict = model_poly(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия третьего порядка<br><sup>(R-squared = {round(r2_score(mean_fingram['Fingram'], model_poly(mean_fingram['Age'])), 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [100]:
model_poly

Polynomial([ 68.87865991,  -4.73006668, -11.84401225,  -2.50609893], domain=[18., 89.], window=[-1.,  1.])

In [101]:
# ЧЕТВЕРТЫЙ ПОРЯДОК

fingram = dependency_data[["Age", "Fingram"]]
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

mean_fingram = pd.DataFrame()
mean_fingram_level = []

for age in fingram["Age"].unique():
    mean_fingram_level.append(np.round(np.mean(fingram["Fingram"][fingram["Age"] == age])))

mean_fingram["Fingram"] = mean_fingram_level
mean_fingram["Age"] = fingram["Age"].unique()

model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 4)

from sklearn.metrics import r2_score

poly_predict = model_poly(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия четвертого порядка<br><sup>(R-squared = {round(r2_score(mean_fingram['Fingram'], model_poly(mean_fingram['Age'])), 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [102]:
# ПЯТЫЙ (по рофлу) ПОРЯДОК

fingram = dependency_data[["Age", "Fingram"]]
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

mean_fingram = pd.DataFrame()
mean_fingram_level = []

for age in fingram["Age"].unique():
    mean_fingram_level.append(np.round(np.mean(fingram["Fingram"][fingram["Age"] == age])))

mean_fingram["Fingram"] = mean_fingram_level
mean_fingram["Age"] = fingram["Age"].unique()

model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 5)

from sklearn.metrics import r2_score

poly_predict = model_poly(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия пятого порядка<br><sup>(R-squared = {round(r2_score(mean_fingram['Fingram'], model_poly(mean_fingram['Age'])), 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [103]:
model_poly

Polynomial([ 67.12988578,  -1.95020079,   5.17995073, -15.1412818 ,
       -19.3295766 ,  11.07293049], domain=[18., 89.], window=[-1.,  1.])

In [104]:
# ДЕВЯТЫЙ ПОРЯДОК

fingram = dependency_data[["Age", "Fingram"]]
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

mean_fingram = pd.DataFrame()
mean_fingram_level = []

for age in fingram["Age"].unique():
    mean_fingram_level.append(np.round(np.mean(fingram["Fingram"][fingram["Age"] == age])))

mean_fingram["Fingram"] = mean_fingram_level
mean_fingram["Age"] = fingram["Age"].unique()

model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 9)

from sklearn.metrics import r2_score

poly_predict = model_poly(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия девятого порядка<br><sup>(R-squared = {round(r2_score(mean_fingram['Fingram'], model_poly(mean_fingram['Age'])), 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

**ОСНОВНАЯ МОДЕЛЬ - ПОЛИНОМИАЛЬНАЯ РЕГРЕССИЯ ВТОРОГО ПОРЯДКА**, по причинам того, что:
* При увеличении порядка регрессии возникает переобучение модели. Особенно заметным процесс оверфиттинга становится после 4 порядка
* В отличие от регресионных моделей третьего, четвертого и дальнейших порядков, график полиномиальной регрессии второго порядка - парабола с ветвями, опущенными вниз. Такая кривая обьясняет нелинейность связи корректнее, чем график кубической параболы или многочлена четвертой степени. 

С точки зрения математического анализа функций, полученных при изменении порядка регрессий, самым логичным обоснованием того, что связь между возрастом и финансовой грамотностью респондентов описывается в виде графика квадратичной функции, является факт отсутствия достаточного финансового опыта у молодых людей, например, еще не закончивших университет, и его приобретение (постепенное возрастание функции) и процесс снижения когнитивных способностей у пожилых людей (отрезок убывания функции).
Так же, опираясь на график параболы, несложно определить пик роста среденего уровня финансовой грамотности у людей. В 45 лет его значение достигает 69.7 процентов -> возможно повышение пика этой финансовой грамотности для того, чтобы убывание шло с большего уровня финансовой грамотности, нежели снйчас

In [105]:
model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 2)
model_poly

Polynomial([ 68.87865991,  -6.27568493, -11.84401225], domain=[18., 89.], window=[-1.,  1.])

In [108]:
# ВТОРОЙ ПОРЯДОК

fingram = dependency_data[["Age", "Fingram"]]
fingram = fingram.sort_values(by = "Age", ascending = True).reset_index()

mean_fingram = pd.DataFrame()
mean_fingram_level = []

for age in fingram["Age"].unique():
    mean_fingram_level.append(np.round(np.mean(fingram["Fingram"][fingram["Age"] == age])))

mean_fingram["Fingram"] = mean_fingram_level
mean_fingram["Age"] = fingram["Age"].unique()

model_poly = poly.Polynomial.fit(mean_fingram["Age"], mean_fingram["Fingram"], 2)

from sklearn.metrics import r2_score

poly_predict = model_poly(mean_fingram["Age"])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.add_annotation(x = 44, y = 69.5, ay = -60, ax = 80,
                   showarrow = True,
                   arrowhead = 4,
                   arrowsize = 1, arrowwidth = 1, arrowcolor = "black")

fig.add_traces(px.scatter(x = [44], y = [69.5]).update_traces(marker_size=17, marker_color=colors[7]).data)

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия второго порядка<br><sup>(R-squared = {round(r2_score(mean_fingram['Fingram'], model_poly(mean_fingram['Age'])), 3)})",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1100)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

**ДОБАВЛЕНИЕ ФАКТОРНОЙ ПЕРЕМЕННОЙ**

In [72]:
dependency_data

Fingram  Age        Age_group                 Education  \
0           57   54        46-55 лет       Среднее специальное   
1           43   47        46-55 лет      Среднее общее и ниже   
2           29   32        26-35 лет      Среднее общее и ниже   
3           86   25        18-25 лет       Среднее специальное   
4           29   65  56 лет и старше  Высшее и неполное высшее   
...        ...  ...              ...                       ...   
12157       86   42        36-45 лет      Среднее общее и ниже   
12158       71   44        36-45 лет      Среднее общее и ниже   
12159       57   18        18-25 лет      Среднее общее и ниже   
12160       43   67  56 лет и старше      Среднее общее и ниже   
12161       86   44        36-45 лет  Высшее и неполное высшее   

      Place_of_living Income  
0               Город  50000  
1               Город  50000  
2               Город  90000  
3               Город  18000  
4               Город  26900  
...               ...    ...  
12157           Город  30000  
12158           Город  20000  
12159           Город  32000  
12160           Город  23800  
12161           Город  58000  

[11828 rows x 6 columns]

In [73]:
weights = np.polyfit(mean_fingram["Age"], mean_fingram["Fingram"], 2)
model = np.poly1d(weights)
results = smf.ols(formula='Fingram ~ model(Age)', data = mean_fingram).fit() # ДОБАВЛЕНИЕ ФАКТОРА

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.751
Model:                            OLS   Adj. R-squared:                  0.748
Method:                 Least Squares   F-statistic:                     211.3
Date:                Mon, 18 Dec 2023   Prob (F-statistic):           7.89e-23
Time:                        17:12:03   Log-Likelihood:                -180.61
No. Observations:                  72   AIC:                             365.2
Df Residuals:                      70   BIC:                             369.8
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept  -5.684e-14      4.474  -1.27e-14      1.000      -8.922       8.922
model(Age)     1.0000      0.069     14.535      0.000       0.863       1.137
==============================================================================
Omnibus:                        0.863   Durbin-Watson:                   1.583
Prob(Omnibus):                  0.650   Jarque-Bera (JB):                0.532
Skew:                           0.207   Prob(JB):                        0.766
Kurtosis:                       3.082   Cond. No.                         819.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [46]:
dependency_data["Family"] = correlation_data["Семейное положение"]
dependency_data

Fingram  Age   Gender        Age_group                 Education  \
0           57   54  ЖЕНСКИЙ        46-55 лет       Среднее специальное   
1           43   47  МУЖСКОЙ        46-55 лет      Среднее общее и ниже   
2           29   32  МУЖСКОЙ        26-35 лет      Среднее общее и ниже   
3           86   25  МУЖСКОЙ        18-25 лет       Среднее специальное   
4           29   65  ЖЕНСКИЙ  56 лет и старше  Высшее и неполное высшее   
...        ...  ...      ...              ...                       ...   
12157       86   42  МУЖСКОЙ        36-45 лет      Среднее общее и ниже   
12158       71   44  ЖЕНСКИЙ        36-45 лет      Среднее общее и ниже   
12159       57   18  ЖЕНСКИЙ        18-25 лет      Среднее общее и ниже   
12160       43   67  ЖЕНСКИЙ  56 лет и старше      Среднее общее и ниже   
12161       86   44  ЖЕНСКИЙ        36-45 лет  Высшее и неполное высшее   

      Place_of_living Income  Preproccesed_Income  \
0               Город  50000                50000   
1               Город  50000                50000   
2               Город  90000                90000   
3               Город  18000                18000   
4               Город  26900                26900   
...               ...    ...                  ...   
12157           Город  30000                30000   
12158           Город  20000                20000   
12159           Город  32000                32000   
12160           Город  23800                23800   
12161           Город  58000                58000   

                                                 Family  
0                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ  
1                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ  
2                                           РАЗВЕДЕН(А)  
3      НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)  
4                     СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ  
...                                                 ...  
12157                                       РАЗВЕДЕН(А)  
12158                                       РАЗВЕДЕН(А)  
12159  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)  
12160                                      ВДОВЕЦ/ВДОВА  
12161                                       РАЗВЕДЕН(А)  

[11828 rows x 9 columns]

In [42]:
preproccesed_income = []

for income in dependency_data["Income"]:
    if income == "НИЧЕГО НЕ ПОЛУЧАЛИ":
        preproccesed_income.append(0)
    elif "e" in income:
        preproccesed_income.append(int(income[0]) * 10 ** int(income[-1]))
    else:
        preproccesed_income.append(int(income))

dependency_data["Preproccesed_Income"] = preproccesed_income
dependency_data

Fingram  Age   Gender        Age_group                 Education  \
0           57   54  ЖЕНСКИЙ        46-55 лет       Среднее специальное   
1           43   47  МУЖСКОЙ        46-55 лет      Среднее общее и ниже   
2           29   32  МУЖСКОЙ        26-35 лет      Среднее общее и ниже   
3           86   25  МУЖСКОЙ        18-25 лет       Среднее специальное   
4           29   65  ЖЕНСКИЙ  56 лет и старше  Высшее и неполное высшее   
...        ...  ...      ...              ...                       ...   
12157       86   42  МУЖСКОЙ        36-45 лет      Среднее общее и ниже   
12158       71   44  ЖЕНСКИЙ        36-45 лет      Среднее общее и ниже   
12159       57   18  ЖЕНСКИЙ        18-25 лет      Среднее общее и ниже   
12160       43   67  ЖЕНСКИЙ  56 лет и старше      Среднее общее и ниже   
12161       86   44  ЖЕНСКИЙ        36-45 лет  Высшее и неполное высшее   

      Place_of_living Income  Preproccesed_Income  
0               Город  50000                50000  
1               Город  50000                50000  
2               Город  90000                90000  
3               Город  18000                18000  
4               Город  26900                26900  
...               ...    ...                  ...  
12157           Город  30000                30000  
12158           Город  20000                20000  
12159           Город  32000                32000  
12160           Город  23800                23800  
12161           Город  58000                58000  

[11828 rows x 8 columns]

In [102]:
most_education = []
most_family = []
most_place = []
mean_income = []
percent_higher_educ = []

for age in dependency_data["Age"].sort_values().reset_index()["Age"].unique():
    most_education.append(dependency_data["Education"][dependency_data["Age"] == age].value_counts().keys()[0])
    most_family.append(dependency_data["Family"][dependency_data["Age"] == age].value_counts().keys()[0])
    most_place.append(dependency_data["Place_of_living"][dependency_data["Age"] == age].value_counts().keys()[0])

    mean_income.append(round(np.mean(dependency_data["Preproccesed_Income"][dependency_data["Age"] == age])))

    percent_higher_educ.append(len(dependency_data[(dependency_data["Education"] == "Высшее и неполное высшее") & (dependency_data["Age"] == age)]) / len(dependency_data["Education"][dependency_data["Age"] == age]) * 100)

In [52]:
education_map = {"Среднее общее и ниже" : 1, "Высшее и неполное высшее" : 2}
place_map = {"Город" : 1, "Село" : 2}
family_map = {"СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ" : 1, "РАЗВЕДЕН(А)" : 2,
              "НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)" : 3, "ВДОВЕЦ/ВДОВА" : 4}

In [ ]:
mean_fingram["Education"] = most_education
mean_fingram["Education_encoded"] = mean_fingram["Education"].map(education_map)

mean_fingram["Family"] = most_family
mean_fingram["Family_encoded"] = mean_fingram["Family"].map(family_map)

mean_fingram["Place_of_living"] = most_place
mean_fingram["Place_of_living_encoded"] = mean_fingram["Place_of_living"].map(place_map)

mean_fingram["Percent_of_university"] = percent_higher_educ

mean_fingram["Income"] = mean_income

mean_fingram

**Первый вариант - уровень образования, которые больше всего распространен у того или иного возраста респондентов**

In [105]:
weights = np.polyfit(mean_fingram["Age"], mean_fingram["Fingram"], 2)
model = np.poly1d(weights)
results = smf.ols(formula='Fingram ~ model(Age) + Education_encoded', data = mean_fingram).fit() # ДОБАВЛЕНИЕ ФАКТОРА ОБРАЗОВАНИЯ

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.789
Model:                            OLS   Adj. R-squared:                  0.783
Method:                 Least Squares   F-statistic:                     129.2
Date:                Mon, 18 Dec 2023   Prob (F-statistic):           4.71e-24
Time:                        17:29:10   Log-Likelihood:                -174.63
No. Observations:                  72   AIC:                             355.3
Df Residuals:                      69   BIC:                             362.1
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
=====================================================================================
                        coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------
Intercept             0.5039      4.149      0.121      0.904      -7.774       8.782
model(Age)            0.9375      0.066     14.164      0.000       0.805       1.070
Education_encoded     2.9025      0.822      3.530      0.001       1.262       4.543
==============================================================================
Omnibus:                        0.846   Durbin-Watson:                   1.870
Prob(Omnibus):                  0.655   Jarque-Bera (JB):                0.349
Skew:                          -0.107   Prob(JB):                        0.840
Kurtosis:                       3.265   Cond. No.                         820.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [106]:
# ДЕВЯТЫЙ ПОРЯДОК
from sklearn.metrics import r2_score

poly_predict = results.predict(mean_fingram[["Age", "Education_encoded"]])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия c дополнительным фактором<br><sup>Мода уровня образования среди людей каждого возраста",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1400)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [107]:
weights = np.polyfit(mean_fingram["Age"], mean_fingram["Fingram"], 2)
model = np.poly1d(weights)
results = smf.ols(formula='Fingram ~ model(Age) + Income', data = mean_fingram).fit() # ДОБАВЛЕНИЕ ФАКТОРА ДОХОДА

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.752
Model:                            OLS   Adj. R-squared:                  0.745
Method:                 Least Squares   F-statistic:                     104.8
Date:                Mon, 18 Dec 2023   Prob (F-statistic):           1.24e-21
Time:                        17:30:58   Log-Likelihood:                -180.44
No. Observations:                  72   AIC:                             366.9
Df Residuals:                      69   BIC:                             373.7
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept      0.5266      4.593      0.115      0.909      -8.637       9.690
model(Age)     0.9787      0.079     12.401      0.000       0.821       1.136
Income      2.998e-05   5.36e-05      0.559      0.578    -7.7e-05       0.000
==============================================================================
Omnibus:                        1.030   Durbin-Watson:                   1.574
Prob(Omnibus):                  0.597   Jarque-Bera (JB):                0.528
Skew:                           0.173   Prob(JB):                        0.768
Kurtosis:                       3.237   Cond. No.                     3.79e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 3.79e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [109]:
# ДЕВЯТЫЙ ПОРЯДОК
from sklearn.metrics import r2_score

poly_predict = results.predict(mean_fingram[["Age", "Income"]])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия c дополнительным фактором<br><sup>Средний доход среди людей каждого возраста",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1400)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

**Процент того или иного типа образования от от общего числа записей о респондентах**

In [299]:
weights = np.polyfit(mean_fingram["Age"], mean_fingram["Fingram"], 2)
model = np.poly1d(weights)
results = smf.ols(formula='Fingram ~ model(Age) + Percent_of_university', data = mean_fingram).fit() # ДОБАВЛЕНИЕ ФАКТОРА

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.789
Model:                            OLS   Adj. R-squared:                  0.783
Method:                 Least Squares   F-statistic:                     129.1
Date:                Mon, 18 Dec 2023   Prob (F-statistic):           4.80e-24
Time:                        01:30:14   Log-Likelihood:                -175.18
No. Observations:                  72   AIC:                             356.4
Df Residuals:                      69   BIC:                             363.2
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
Intercept                 2.2799      4.185      0.545      0.588      -6.068      10.628
model(Age)                0.9168      0.068     13.461      0.000       0.781       1.053
Percent_of_university     0.1141      0.033      3.471      0.001       0.049       0.180
==============================================================================
Omnibus:                        2.804   Durbin-Watson:                   1.898
Prob(Omnibus):                  0.246   Jarque-Bera (JB):                2.012
Skew:                          -0.330   Prob(JB):                        0.366
Kurtosis:                       3.486   Cond. No.                         889.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [300]:
results.params

Intercept                2.279858
model(Age)               0.916775
Percent_of_university    0.114133
dtype: float64

In [303]:
# ДЕВЯТЫЙ ПОРЯДОК
from sklearn.metrics import r2_score

poly_predict = results.predict(mean_fingram[["Age", "Percent_of_university"]])

fig = go.Figure()   

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия c дополнительной независимой переменной<br><sup>Уровень образования в виде процента одного из видов образования от общего числа записей",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1400)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [232]:
dependency_data["Education"][(dependency_data["Age"] >= 40) & (dependency_data["Age"] <= 70)].value_counts()

Среднее общее и ниже        3096
Среднее специальное         1879
Высшее и неполное высшее    1674
НЕТ ОТВЕТА                     6
ЗАТРУДНЯЮСЬ ОТВЕТИТЬ           1
ОТКАЗ ОТ ОТВЕТА                1
Name: Education, dtype: int64

In [267]:
dependency_data["Education"][dependency_data["Age"] == 45]

48            Среднее специальное
115      Высшее и неполное высшее
309           Среднее специальное
343          Среднее общее и ниже
400          Среднее общее и ниже
                   ...           
11924        Среднее общее и ниже
11985        Среднее общее и ниже
12070        Среднее общее и ниже
12088        Среднее общее и ниже
12148    Высшее и неполное высшее
Name: Education, Length: 197, dtype: object

In [268]:
52 / 197 * 100

26.39593908629442

In [231]:
dependency_data["Education"][(dependency_data["Age"] >= 23) & (dependency_data["Age"] <= 40)].value_counts()

Высшее и неполное высшее    1416
Среднее общее и ниже        1260
Среднее специальное          791
ЗАТРУДНЯЮСЬ ОТВЕТИТЬ           6
ОТКАЗ ОТ ОТВЕТА                2
НЕТ ОТВЕТА                     1
Name: Education, dtype: int64

**Влияние нескольких дополнительных независимых переменных**

In [313]:
weights = np.polyfit(mean_fingram["Age"], mean_fingram["Fingram"], 2)
model = np.poly1d(weights)
results = smf.ols(formula='Fingram ~ model(Age) + Education_encoded + Family_encoded + Place_of_living_encoded', data = mean_fingram).fit() # ДОБАВЛЕНИЕ ФАКТОРА

results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.793
Model:                            OLS   Adj. R-squared:                  0.784
Method:                 Least Squares   F-statistic:                     86.78
Date:                Mon, 18 Dec 2023   Prob (F-statistic):           3.34e-23
Time:                        01:38:56   Log-Likelihood:                -174.53
No. Observations:                  72   AIC:                             357.1
Df Residuals:                      68   BIC:                             366.2
Df Model:                           3                                         
Covariance Type:            nonrobust                                         
===========================================================================================
                              coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------
Intercept                   2.6381      3.765      0.701      0.486      -4.874      10.150
model(Age)                  0.8673      0.112      7.713      0.000       0.643       1.092
Education_encoded           3.2412      0.908      3.569      0.001       1.429       5.053
Family_encoded             -0.3419      0.449     -0.761      0.449      -1.238       0.555
Place_of_living_encoded     2.6381      3.765      0.701      0.486      -4.874      10.150
==============================================================================
Omnibus:                        0.882   Durbin-Watson:                   1.975
Prob(Omnibus):                  0.643   Jarque-Bera (JB):                0.373
Skew:                          -0.110   Prob(JB):                        0.830
Kurtosis:                       3.276   Cond. No.                     2.33e+18
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The smallest eigenvalue is 5.59e-32. This might indicate that there are
strong multicollinearity problems or that the design matrix is singular.
"""

In [314]:
# ДЕВЯТЫЙ ПОРЯДОК
from sklearn.metrics import r2_score

poly_predict = results.predict(mean_fingram[["Age", "Education_encoded", "Family_encoded", "Place_of_living_encoded"]])

fig = go.Figure()

fig = px.scatter(x = mean_fingram["Age"], y = mean_fingram["Fingram"], color_discrete_sequence=[colors[9]])
fig.add_trace(go.Scatter(x = mean_fingram["Age"], y = poly_predict, name = "Полиномиальная регрессия"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия c дополнительными факторными переменными<br><sup>Уровень образования, семейное положение, место жительства",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 120))
fig.update_layout(yaxis_range=[0, 100])
fig.update_layout(height = 800, width = 1400)
fig.update_layout(showlegend=False)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

**ОБСУЖДЕНИЕ ПРОШЛО**:

* Используем весь датасет полностью для того, чтобы не терять вариативность и количество наблюдений
* Строим полиномиальную и линейную регрессии от возраста - объясняем все пункты (порядок, убывание, возрастание, пиковое значение)
* Кодируем категориальные переменные по методу one hot encoding
* Строим полную многофакторную полиномиальную регрессионную модель на следующих объясняющих переменных: образование, семейное положение, доход, место жительства, пол
* Строим многофакторную линейную регрессию по тем же факторам
* Находим статзначимые и не статзначимые факторы - объясняем


1. Подготовка датасета

In [222]:
# СОЗДАНИЕ ДАТАСЕТА С НЕОБХОДИМЫМИ СТОЛБЦАМИ
regression_data = pd.DataFrame()

regression_data["ID"] = data["ID"]

regression_data["Age"] = data["Age"]
regression_data["Age_Group"] = data["Age group"]
regression_data["Fingram"] = coeffs["Financial level %"]

regression_data["Education"] = data["Education"]
regression_data["Place_of_living"] = data["Type of residence"]
regression_data["Relationship"] = data["Relationship"]
regression_data["Gender"] = data["Gender"]

regression_data["Income"] = data_archive["k66a"]

regression_data

ID  Age        Age_Group  Fingram                 Education  \
0         1000101   54        46-55 лет       57       Среднее специальное   
1         1000102   47        46-55 лет       43      Среднее общее и ниже   
2         1000502   32        26-35 лет       29      Среднее общее и ниже   
3         1000604   25        18-25 лет       86       Среднее специальное   
4         1000701   65  56 лет и старше       29  Высшее и неполное высшее   
...           ...  ...              ...      ...                       ...   
12157  1351071205   42        36-45 лет       86      Среднее общее и ниже   
12158   138930501   44        36-45 лет       71      Среднее общее и ниже   
12159   138930502   18        18-25 лет       57      Среднее общее и ниже   
12160   138930505   67  56 лет и старше       43      Среднее общее и ниже   
12161  1429041401   44        36-45 лет       86  Высшее и неполное высшее   

      Place_of_living                                      Relationship  \
0               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
1               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
2               Город                                       РАЗВЕДЕН(А)   
3               Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
4               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
...               ...                                               ...   
12157           Город                                       РАЗВЕДЕН(А)   
12158           Город                                       РАЗВЕДЕН(А)   
12159           Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
12160           Город                                      ВДОВЕЦ/ВДОВА   
12161           Город                                       РАЗВЕДЕН(А)   

        Gender Income  
0      ЖЕНСКИЙ  50000  
1      МУЖСКОЙ  50000  
2      МУЖСКОЙ  90000  
3      МУЖСКОЙ  18000  
4      ЖЕНСКИЙ  26900  
...        ...    ...  
12157  МУЖСКОЙ  30000  
12158  ЖЕНСКИЙ  20000  
12159  ЖЕНСКИЙ  32000  
12160  ЖЕНСКИЙ  23800  
12161  ЖЕНСКИЙ  58000  

[12162 rows x 9 columns]

1.1 Отчистка датасета

In [223]:
regression_data = regression_data.dropna()
regression_data

ID  Age        Age_Group  Fingram                 Education  \
0         1000101   54        46-55 лет       57       Среднее специальное   
1         1000102   47        46-55 лет       43      Среднее общее и ниже   
2         1000502   32        26-35 лет       29      Среднее общее и ниже   
3         1000604   25        18-25 лет       86       Среднее специальное   
4         1000701   65  56 лет и старше       29  Высшее и неполное высшее   
...           ...  ...              ...      ...                       ...   
12157  1351071205   42        36-45 лет       86      Среднее общее и ниже   
12158   138930501   44        36-45 лет       71      Среднее общее и ниже   
12159   138930502   18        18-25 лет       57      Среднее общее и ниже   
12160   138930505   67  56 лет и старше       43      Среднее общее и ниже   
12161  1429041401   44        36-45 лет       86  Высшее и неполное высшее   

      Place_of_living                                      Relationship  \
0               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
1               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
2               Город                                       РАЗВЕДЕН(А)   
3               Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
4               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
...               ...                                               ...   
12157           Город                                       РАЗВЕДЕН(А)   
12158           Город                                       РАЗВЕДЕН(А)   
12159           Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
12160           Город                                      ВДОВЕЦ/ВДОВА   
12161           Город                                       РАЗВЕДЕН(А)   

        Gender Income  
0      ЖЕНСКИЙ  50000  
1      МУЖСКОЙ  50000  
2      МУЖСКОЙ  90000  
3      МУЖСКОЙ  18000  
4      ЖЕНСКИЙ  26900  
...        ...    ...  
12157  МУЖСКОЙ  30000  
12158  ЖЕНСКИЙ  20000  
12159  ЖЕНСКИЙ  32000  
12160  ЖЕНСКИЙ  23800  
12161  ЖЕНСКИЙ  58000  

[11877 rows x 9 columns]

In [224]:
regression_data = regression_data[regression_data["Age"] < 90]
regression_data

ID  Age        Age_Group  Fingram                 Education  \
0         1000101   54        46-55 лет       57       Среднее специальное   
1         1000102   47        46-55 лет       43      Среднее общее и ниже   
2         1000502   32        26-35 лет       29      Среднее общее и ниже   
3         1000604   25        18-25 лет       86       Среднее специальное   
4         1000701   65  56 лет и старше       29  Высшее и неполное высшее   
...           ...  ...              ...      ...                       ...   
12157  1351071205   42        36-45 лет       86      Среднее общее и ниже   
12158   138930501   44        36-45 лет       71      Среднее общее и ниже   
12159   138930502   18        18-25 лет       57      Среднее общее и ниже   
12160   138930505   67  56 лет и старше       43      Среднее общее и ниже   
12161  1429041401   44        36-45 лет       86  Высшее и неполное высшее   

      Place_of_living                                      Relationship  \
0               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
1               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
2               Город                                       РАЗВЕДЕН(А)   
3               Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
4               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
...               ...                                               ...   
12157           Город                                       РАЗВЕДЕН(А)   
12158           Город                                       РАЗВЕДЕН(А)   
12159           Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
12160           Город                                      ВДОВЕЦ/ВДОВА   
12161           Город                                       РАЗВЕДЕН(А)   

        Gender Income  
0      ЖЕНСКИЙ  50000  
1      МУЖСКОЙ  50000  
2      МУЖСКОЙ  90000  
3      МУЖСКОЙ  18000  
4      ЖЕНСКИЙ  26900  
...        ...    ...  
12157  МУЖСКОЙ  30000  
12158  ЖЕНСКИЙ  20000  
12159  ЖЕНСКИЙ  32000  
12160  ЖЕНСКИЙ  23800  
12161  ЖЕНСКИЙ  58000  

[11828 rows x 9 columns]

1.2 Обработка столбцов

1.2.1 Перевод в корректный вид столбца с доходами

In [225]:
preproccesed_income = []

for income in regression_data["Income"]:
    if income == "НИЧЕГО НЕ ПОЛУЧАЛИ":
        preproccesed_income.append(0)
    elif "e" in income:
        preproccesed_income.append(int(income[0]) * 10 ** int(income[-1]))
    else:
        preproccesed_income.append(int(income))

regression_data["Income"] = preproccesed_income
regression_data

ID  Age        Age_Group  Fingram                 Education  \
0         1000101   54        46-55 лет       57       Среднее специальное   
1         1000102   47        46-55 лет       43      Среднее общее и ниже   
2         1000502   32        26-35 лет       29      Среднее общее и ниже   
3         1000604   25        18-25 лет       86       Среднее специальное   
4         1000701   65  56 лет и старше       29  Высшее и неполное высшее   
...           ...  ...              ...      ...                       ...   
12157  1351071205   42        36-45 лет       86      Среднее общее и ниже   
12158   138930501   44        36-45 лет       71      Среднее общее и ниже   
12159   138930502   18        18-25 лет       57      Среднее общее и ниже   
12160   138930505   67  56 лет и старше       43      Среднее общее и ниже   
12161  1429041401   44        36-45 лет       86  Высшее и неполное высшее   

      Place_of_living                                      Relationship  \
0               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
1               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
2               Город                                       РАЗВЕДЕН(А)   
3               Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
4               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
...               ...                                               ...   
12157           Город                                       РАЗВЕДЕН(А)   
12158           Город                                       РАЗВЕДЕН(А)   
12159           Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
12160           Город                                      ВДОВЕЦ/ВДОВА   
12161           Город                                       РАЗВЕДЕН(А)   

        Gender  Income  
0      ЖЕНСКИЙ   50000  
1      МУЖСКОЙ   50000  
2      МУЖСКОЙ   90000  
3      МУЖСКОЙ   18000  
4      ЖЕНСКИЙ   26900  
...        ...     ...  
12157  МУЖСКОЙ   30000  
12158  ЖЕНСКИЙ   20000  
12159  ЖЕНСКИЙ   32000  
12160  ЖЕНСКИЙ   23800  
12161  ЖЕНСКИЙ   58000  

[11828 rows x 9 columns]

1.2.2 Кодирование категориальных столбцов

In [226]:
regression_data = regression_data[(regression_data["Education"] != "ОТКАЗ ОТ ОТВЕТА") & (regression_data["Education"] != "НЕТ ОТВЕТА") & (regression_data["Education"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ")]
regression_data = regression_data[(regression_data["Relationship"] != "ОТКАЗ ОТ ОТВЕТА") & (regression_data["Relationship"] != "НЕТ ОТВЕТА") & (regression_data["Relationship"] != "ЗАТРУДНЯЮСЬ ОТВЕТИТЬ")]
regression_data

ID  Age        Age_Group  Fingram                 Education  \
0         1000101   54        46-55 лет       57       Среднее специальное   
1         1000102   47        46-55 лет       43      Среднее общее и ниже   
2         1000502   32        26-35 лет       29      Среднее общее и ниже   
3         1000604   25        18-25 лет       86       Среднее специальное   
4         1000701   65  56 лет и старше       29  Высшее и неполное высшее   
...           ...  ...              ...      ...                       ...   
12157  1351071205   42        36-45 лет       86      Среднее общее и ниже   
12158   138930501   44        36-45 лет       71      Среднее общее и ниже   
12159   138930502   18        18-25 лет       57      Среднее общее и ниже   
12160   138930505   67  56 лет и старше       43      Среднее общее и ниже   
12161  1429041401   44        36-45 лет       86  Высшее и неполное высшее   

      Place_of_living                                      Relationship  \
0               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
1               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
2               Город                                       РАЗВЕДЕН(А)   
3               Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
4               Город                 СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ   
...               ...                                               ...   
12157           Город                                       РАЗВЕДЕН(А)   
12158           Город                                       РАЗВЕДЕН(А)   
12159           Город  НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)   
12160           Город                                      ВДОВЕЦ/ВДОВА   
12161           Город                                       РАЗВЕДЕН(А)   

        Gender  Income  
0      ЖЕНСКИЙ   50000  
1      МУЖСКОЙ   50000  
2      МУЖСКОЙ   90000  
3      МУЖСКОЙ   18000  
4      ЖЕНСКИЙ   26900  
...        ...     ...  
12157  МУЖСКОЙ   30000  
12158  ЖЕНСКИЙ   20000  
12159  ЖЕНСКИЙ   32000  
12160  ЖЕНСКИЙ   23800  
12161  ЖЕНСКИЙ   58000  

[11766 rows x 9 columns]

In [227]:
education_encoded = pd.get_dummies(regression_data["Education"])
regression_data = regression_data.drop(["Education"], axis = 1)
regression_data = regression_data.join(education_encoded)

place_of_living_encoded = pd.get_dummies(regression_data["Place_of_living"])
regression_data = regression_data.drop(["Place_of_living"], axis = 1)
regression_data = regression_data.join(place_of_living_encoded)

relationship_encoded = pd.get_dummies(regression_data["Relationship"])
regression_data = regression_data.drop(["Relationship"], axis = 1)
regression_data = regression_data.join(relationship_encoded)

gender_encoded = pd.get_dummies(regression_data["Gender"])
regression_data = regression_data.drop(["Gender"], axis = 1)
regression_data = regression_data.join(gender_encoded)

regression_data

ID  Age        Age_Group  Fingram  Income  \
0         1000101   54        46-55 лет       57   50000   
1         1000102   47        46-55 лет       43   50000   
2         1000502   32        26-35 лет       29   90000   
3         1000604   25        18-25 лет       86   18000   
4         1000701   65  56 лет и старше       29   26900   
...           ...  ...              ...      ...     ...   
12157  1351071205   42        36-45 лет       86   30000   
12158   138930501   44        36-45 лет       71   20000   
12159   138930502   18        18-25 лет       57   32000   
12160   138930505   67  56 лет и старше       43   23800   
12161  1429041401   44        36-45 лет       86   58000   

       Высшее и неполное высшее  Среднее общее и ниже  Среднее специальное  \
0                             0                     0                    1   
1                             0                     1                    0   
2                             0                     1                    0   
3                             0                     0                    1   
4                             1                     0                    0   
...                         ...                   ...                  ...   
12157                         0                     1                    0   
12158                         0                     1                    0   
12159                         0                     1                    0   
12160                         0                     1                    0   
12161                         1                     0                    0   

       Город  Село  ВДОВЕЦ/ВДОВА  \
0          1     0             0   
1          1     0             0   
2          1     0             0   
3          1     0             0   
4          1     0             0   
...      ...   ...           ...   
12157      1     0             0   
12158      1     0             0   
12159      1     0             0   
12160      1     0             1   
12161      1     0             0   

       НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)  РАЗВЕДЕН(А)  \
0                                                     0            0   
1                                                     0            0   
2                                                     0            1   
3                                                     1            0   
4                                                     0            0   
...                                                 ...          ...   
12157                                                 0            1   
12158                                                 0            1   
12159                                                 1            0   
12160                                                 0            0   
12161                                                 0            1   

       СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ  ЖЕНСКИЙ  МУЖСКОЙ  
0                                      1        1        0  
1                                      1        0        1  
2                                      0        0        1  
3                                      0        0        1  
4                                      1        1        0  
...                                  ...      ...      ...  
12157                                  0        0        1  
12158                                  0        1        0  
12159                                  0        1        0  
12160                                  0        1        0  
12161                                  0        1        0  

[11766 rows x 16 columns]

2. Построение регрессий

In [228]:
regression_data = regression_data.sort_values(by = "Age", ascending = True).reset_index()

In [229]:
lin_model = smf.ols("Fingram ~ Age", data = regression_data)
lin_model = lin_model.fit()

weights = np.polyfit(regression_data["Age"], regression_data["Fingram"], 2)
model = np.poly1d(weights)
poly_model = smf.ols(formula = 'Fingram ~ model(Age)', data = regression_data)
poly_model = poly_model.fit()

poly_predict = poly_model.predict(regression_data["Age"])
lin_predict = lin_model.predict(regression_data["Age"])

fig = go.Figure()

point_counts = regression_data.groupby(["Age", "Fingram"]).size().reset_index(name = "count")
fig = px.scatter(x = regression_data["Age"], y = regression_data["Fingram"], color_discrete_sequence=["#74777B"])
fig = px.scatter(point_counts, x = "Age", y = "Fingram",
                 color = "count", color_continuous_scale=["rgba(0, 0, 0, 0)", "rgba(0, 0, 0, 255)"])
fig.add_trace(go.Scatter(x = regression_data["Age"], y = poly_predict, name = "Полиномиальная регрессия", marker_color = "#0000ff"))
fig.add_trace(go.Scatter(x = regression_data["Age"], y = lin_predict, name = "Линейная регрессия", marker_color = "#ff0000"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Сравнение полиномиальной и линейной регрессий<br><sup>R2 линейной регрессии = {round(lin_model.rsquared, 4)}, R2 полиномиальной регрессии = {round(poly_model.rsquared, 4)}",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[-2, 102], xaxis_range = [14, 95])
fig.update_layout(coloraxis_showscale=False)
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [230]:
poly_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.017
Model:                            OLS   Adj. R-squared:                  0.017
Method:                 Least Squares   F-statistic:                     201.8
Date:                Wed, 20 Dec 2023   Prob (F-statistic):           1.97e-45
Time:                        00:30:47   Log-Likelihood:                -54130.
No. Observations:               11766   AIC:                         1.083e+05
Df Residuals:                   11764   BIC:                         1.083e+05
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept  -7.284e-13      4.688  -1.55e-13      1.000      -9.189       9.189
model(Age)     1.0000      0.070     14.207      0.000       0.862       1.138
==============================================================================
Omnibus:                      684.822   Durbin-Watson:                   1.983
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              513.971
Skew:                          -0.417   Prob(JB):                    2.47e-112
Kurtosis:                       2.405   Cond. No.                     1.41e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.41e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [205]:
lin_model = smf.ols("Fingram ~ Age", data = regression_data)
lin_model = lin_model.fit()

weights = np.polyfit(regression_data["Age"], regression_data["Fingram"], 4)
model = np.poly1d(weights)
poly_model = smf.ols(formula = 'Fingram ~ model(Age)', data = regression_data)
poly_model = poly_model.fit()

poly_predict = poly_model.predict(regression_data["Age"])

fig = go.Figure()

point_counts = regression_data.groupby(["Age", "Fingram"]).size().reset_index(name = "count")

fig.add_trace(go.Scatter(x = regression_data["Age"], y = poly_predict, name = "Полиномиальная регрессия", marker_color = "#0088BB"))

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия четвертого порядка",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[-2, 102], xaxis_range = [14, 95])
fig.update_layout(coloraxis_showscale=False)
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [166]:
poly_model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.017
Model:                            OLS   Adj. R-squared:                  0.017
Method:                 Least Squares   F-statistic:                     201.8
Date:                Tue, 19 Dec 2023   Prob (F-statistic):           1.97e-45
Time:                        20:56:56   Log-Likelihood:                -54130.
No. Observations:               11766   AIC:                         1.083e+05
Df Residuals:                   11764   BIC:                         1.083e+05
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept  -7.284e-13      4.688  -1.55e-13      1.000      -9.189       9.189
model(Age)     1.0000      0.070     14.207      0.000       0.862       1.138
==============================================================================
Omnibus:                      684.822   Durbin-Watson:                   1.983
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              513.971
Skew:                          -0.417   Prob(JB):                    2.47e-112
Kurtosis:                       2.405   Cond. No.                     1.41e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.41e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [167]:
weights = np.polyfit(regression_data["Age"], regression_data["Fingram"], 2)
model = np.poly1d(weights)
poly_model_2 = smf.ols(formula = 'Fingram ~ model(Age)', data = regression_data)
poly_model_2 = poly_model_2.fit()

In [168]:
y_2 = []
y_3 = []
y_4 = []

# ФУНКЦИИ ПОЛУЧЕНЫ ЧЕРЕЗ np.polyfit
for x in range(-1000, 1200):
    y_2.append(68.35992551085126 - 5.972935979516379 * (-1.5070422535211268 + 0.028169014084507043 * x) - 10.143205986019701 * (-1.5070422535211268 + 0.028169014084507043 * x)  ** 2)
    y_3.append(68.332917404667 - 6.422704809224731 * (-1.5070422535211268 + 0.028169014084507043 * x) - 9.963991666208852 * (-1.5070422535211268 + 0.028169014084507043 * x) ** 2 + 0.936185183360263 * (-1.5070422535211268+0.028169014084507043 * x) ** 3)
for x in range(-150, 250):
    y_4.append(66.82831431841734 - 4.50244793996895 * (-1.5070422535211268 + 0.028169014084507043 * x) + 7.817776785453828 * (-1.5070422535211268 + 0.028169014084507043 * x) ** 2 - 3.4474442508602126 * (-1.5070422535211268 + 0.028169014084507043 * x) ** 3 - 23.16894601407638 * (-1.5070422535211268 + 0.028169014084507043 * x) ** 4)

fig = go.Figure()

point_counts = regression_data.groupby(["Age", "Fingram"]).size().reset_index(name = "count")

fig.add_trace(go.Scatter(x = list(range(-1000, 1200)), y = y_2, name = "Второй порядок", marker_color = "#0088BB"))
fig.add_trace(go.Scatter(x = list(range(-1000, 1200)), y = y_3, name = "Третий порядок", marker_color = "#0000ff"))
fig.add_trace(go.Scatter(x = list(range(-50, 700)), y = y_4, name = "Четвертый порядок", marker_color = colors[9]))

fig.update_yaxes(title = "Y", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "X", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия четвертого порядка",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
#fig.update_layout(yaxis_range=[-2, 102], xaxis_range = [-20, 130])
fig.update_layout(coloraxis_showscale=False)
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [169]:
lin_model = smf.ols("Fingram ~ Age", data = regression_data)
lin_model = lin_model.fit()

weights = np.polyfit(regression_data["Age"], regression_data["Fingram"], 2)
model = np.poly1d(weights)
poly_model = smf.ols(formula = 'Fingram ~ model(Age)', data = regression_data)
poly_model = poly_model.fit()

poly_predict = poly_model.predict(regression_data["Age"])

fig = go.Figure()

point_counts = regression_data.groupby(["Age", "Fingram"]).size().reset_index(name = "count")

fig.add_trace(go.Scatter(x = regression_data["Age"], y = poly_predict, name = "Полиномиальная регрессия", marker_color = "#0088BB"))

fig.add_vrect(x0 = 18, x1 = 37, line_width = 0, fillcolor = colors[7], opacity = 0.2, layer="below")

fig.add_vrect(x0 = 70, x1 = 89, line_width = 0, fillcolor = colors[7], opacity = 0.2, layer="below")

fig.add_vline(x = 44, y0 = 0, y1 = 0.69, line_width = 3, line_color= "#555555", line_dash = "dash")

fig.add_annotation(x = 44.5, y = 71, ay = -60, ax = 80, font = dict(family = "Arial", color = "black", size = 16),
                   showarrow = True,
                   arrowhead = 4,
                   arrowsize = 1, arrowwidth = 1, arrowcolor = "black")


fig.add_traces(px.scatter(x = [44], y = [69.2]).update_traces(marker_size=17, marker_color="#0088BB").data)

fig.update_yaxes(title = "Индекс финансовой грамотности, %", title_font = dict(size = 22, family = 'Arial', color = 'black'))
fig.update_xaxes(title = "Возраст", title_font = dict(size = 22, family = 'Arial', color = 'black'))

fig.update_layout(title = f"Полиномиальная регрессия второго порядка",
                  font_family = "Arial",
                  font_color = "black",
                  title_font_size = 32)

fig.update_layout(margin=dict(t = 100))
fig.update_layout(yaxis_range=[0, 100], xaxis_range = [13, 95])
fig.update_layout(coloraxis_showscale=False)
fig.update_layout(height = 800, width = 1300)
fig.update_layout(font_family = "Arial", font_size = 22, title_font_family = "Arial", font_color = "black")

fig.show()

In [170]:
point_counts["count"]

0       8
1       3
2      13
3      22
4      19
       ..
506     3
507     2
508     6
509     4
510     1
Name: count, Length: 511, dtype: int64

**ОБЪЯСНЕНИЕ ВСЕГО ЧТО НЕОБХОДИМО (порядок, убывание, возрастание, пиковое значение + демонстрация графиков функций)**

3. Проведение многофакторного анализа

3.1 Построение многофакторной полиномиальной регрессии

In [231]:
columns_map = {"Высшее и неполное высшее" : "Высшее_и_неполное_высшее",
               "Среднее общее и ниже" : "Среднее_общее_и_ниже",
               "Среднее специальное" : "Среднее_специальное",
               "НИКОГДА В ЗАРЕГИСТРИРОВАННОМ БРАКЕ НЕ СОСТОЯЛ(А)" : "НИКОГДА_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ_НЕ_СОСТОЯЛ_А",
               "СОСТОЮ В ЗАРЕГИСТРИРОВАННОМ БРАКЕ" : "СОСТОЮ_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ",
               "ВДОВЕЦ/ВДОВА" : "ВДОВЕЦ_ВДОВА", 
               "РАЗВЕДЕН(А)" : "РАЗВЕДЕН_А"}
regression_data = regression_data.rename(mapper = columns_map, axis = 1)

regression_data

index         ID  Age        Age_Group  Fingram  Income  \
0      10038   33902804   18        18-25 лет       43   11000   
1       6651  116044703   18        18-25 лет       86     930   
2      10249   48901503   18        18-25 лет       86       0   
3       7269  129021004   18        18-25 лет       86       0   
4      10126   39904002   18        18-25 лет       14       0   
...      ...        ...  ...              ...      ...     ...   
11761   8768  141044702   89  56 лет и старше       43   20000   
11762   5594   93022401   89  56 лет и старше       57   36400   
11763   5481   93011706   89  56 лет и старше       14   19000   
11764   9649  161203901   89  56 лет и старше       71   25881   
11765   2666   52017707   89  56 лет и старше       29   26000   

       Высшее_и_неполное_высшее  Среднее_общее_и_ниже  Среднее_специальное  \
0                             0                     0                    1   
1                             0                     1                    0   
2                             1                     0                    0   
3                             0                     1                    0   
4                             0                     1                    0   
...                         ...                   ...                  ...   
11761                         0                     1                    0   
11762                         1                     0                    0   
11763                         0                     1                    0   
11764                         0                     0                    1   
11765                         0                     1                    0   

       Город  Село  ВДОВЕЦ_ВДОВА  \
0          0     1             0   
1          1     0             0   
2          1     0             0   
3          0     1             0   
4          0     1             0   
...      ...   ...           ...   
11761      1     0             1   
11762      0     1             1   
11763      0     1             1   
11764      1     0             1   
11765      0     1             1   

       НИКОГДА_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ_НЕ_СОСТОЯЛ_А  РАЗВЕДЕН_А  \
0                                                    1           0   
1                                                    1           0   
2                                                    1           0   
3                                                    1           0   
4                                                    1           0   
...                                                ...         ...   
11761                                                0           0   
11762                                                0           0   
11763                                                0           0   
11764                                                0           0   
11765                                                0           0   

       СОСТОЮ_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ  ЖЕНСКИЙ  МУЖСКОЙ  
0                                      0        0        1  
1                                      0        0        1  
2                                      0        1        0  
3                                      0        1        0  
4                                      0        1        0  
...                                  ...      ...      ...  
11761                                  0        1        0  
11762                                  0        1        0  
11763                                  0        0        1  
11764                                  0        1        0  
11765                                  0        1        0  

[11766 rows x 17 columns]

In [232]:
regression_data.columns

Index(['index', 'ID', 'Age', 'Age_Group', 'Fingram', 'Income',
       'Высшее_и_неполное_высшее', 'Среднее_общее_и_ниже',
       'Среднее_специальное', 'Город', 'Село', 'ВДОВЕЦ_ВДОВА',
       'НИКОГДА_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ_НЕ_СОСТОЯЛ_А', 'РАЗВЕДЕН_А',
       'СОСТОЮ_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ', 'ЖЕНСКИЙ', 'МУЖСКОЙ'],
      dtype='object')

In [236]:
weights = np.polyfit(regression_data["Age"], regression_data["Fingram"], 2)
model = np.poly1d(weights)
formula = "Fingram ~ model(Age) + Income + Среднее_общее_и_ниже + Среднее_специальное +  Город  + МУЖСКОЙ"
poly_model_multi = smf.ols(formula = formula, data = regression_data)
poly_model_multi= poly_model_multi.fit()
poly_model_multi.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.143
Model:                            OLS   Adj. R-squared:                  0.143
Method:                 Least Squares   F-statistic:                     328.2
Date:                Wed, 20 Dec 2023   Prob (F-statistic):               0.00
Time:                        00:35:37   Log-Likelihood:                -53319.
No. Observations:               11766   AIC:                         1.067e+05
Df Residuals:                   11759   BIC:                         1.067e+05
Df Model:                           6                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
Intercept               16.6244      4.501      3.694      0.000       7.802      25.446
model(Age)               0.7467      0.067     11.146      0.000       0.615       0.878
Income                4.506e-05   7.49e-06      6.015      0.000    3.04e-05    5.97e-05
Среднее_общее_и_ниже   -14.7935      0.525    -28.164      0.000     -15.823     -13.764
Среднее_специальное     -7.9549      0.575    -13.827      0.000      -9.083      -6.827
Город                   10.3387      0.479     21.566      0.000       9.399      11.278
МУЖСКОЙ                  0.3838      0.432      0.888      0.375      -0.464       1.231
==============================================================================
Omnibus:                      408.082   Durbin-Watson:                   1.988
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              385.766
Skew:                          -0.397   Prob(JB):                     1.71e-84
Kurtosis:                       2.606   Cond. No.                     9.05e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 9.05e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [238]:
weights = np.polyfit(regression_data["Age"], regression_data["Fingram"], 2)
model = np.poly1d(weights)
formula = "Fingram ~ model(Age) + Income + Среднее_общее_и_ниже + Среднее_специальное + МУЖСКОЙ + ВДОВЕЦ_ВДОВА + НИКОГДА_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ_НЕ_СОСТОЯЛ_А + РАЗВЕДЕН_А + СОСТОЮ_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ"
poly_model_multi = smf.ols(formula = formula, data = regression_data)
poly_model_multi= poly_model_multi.fit()
poly_model_multi.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.111
Model:                            OLS   Adj. R-squared:                  0.110
Method:                 Least Squares   F-statistic:                     183.5
Date:                Wed, 20 Dec 2023   Prob (F-statistic):          2.11e-293
Time:                        00:57:03   Log-Likelihood:                -53538.
No. Observations:               11766   AIC:                         1.071e+05
Df Residuals:                   11757   BIC:                         1.072e+05
Df Model:                           8                                         
Covariance Type:            nonrobust                                         
===================================================================================================================
                                                      coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------------------------
Intercept                                          28.2133      4.011      7.034      0.000      20.351      36.076
model(Age)                                          0.5819      0.076      7.694      0.000       0.434       0.730
Income                                           6.053e-05   7.63e-06      7.929      0.000    4.56e-05    7.55e-05
Среднее_общее_и_ниже                              -16.2389      0.531    -30.572      0.000     -17.280     -15.198
Среднее_специальное                                -8.7586      0.586    -14.954      0.000      -9.907      -7.611
МУЖСКОЙ                                            -0.1585      0.456     -0.347      0.728      -1.053       0.736
ВДОВЕЦ_ВДОВА                                        5.5480      0.919      6.036      0.000       3.746       7.350
НИКОГДА_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ_НЕ_СОСТОЯЛ_А     7.6906      1.152      6.675      0.000       5.432       9.949
РАЗВЕДЕН_А                                          6.5782      1.194      5.508      0.000       4.237       8.919
СОСТОЮ_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ                   8.3964      1.117      7.515      0.000       6.206      10.587
==============================================================================
Omnibus:                      423.326   Durbin-Watson:                   1.990
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              379.710
Skew:                          -0.382   Prob(JB):                     3.52e-83
Kurtosis:                       2.564   Cond. No.                     3.49e+19
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The smallest eigenvalue is 1.68e-26. This might indicate that there are
strong multicollinearity problems or that the design matrix is singular.
"""

Тест на гомоскедатичность

In [243]:
poly_model_multi.resid

0       -22.006977
1        29.082728
2        12.741624
3        28.980481
4       -43.019519
           ...    
11761    -6.135653
11762    -9.367127
11763   -34.916592
11764    14.028184
11765   -20.498805
Length: 11766, dtype: float64

In [244]:
poly_model_multi.model.exog

array([[1.00000000e+00, 6.41896555e+01, 1.10000000e+04, ...,
        1.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [1.00000000e+00, 6.41896555e+01, 9.30000000e+02, ...,
        1.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [1.00000000e+00, 6.41896555e+01, 0.00000000e+00, ...,
        1.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       ...,
       [1.00000000e+00, 5.22437835e+01, 1.90000000e+04, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [1.00000000e+00, 5.22437835e+01, 2.58810000e+04, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [1.00000000e+00, 5.22437835e+01, 2.60000000e+04, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00]])

In [ ]:
from statsmodels.stats.diagnostic import het_white
white_test = het_white(poly_model_multi.resid,  poly_model_multi.model.exog)
labels = ['Test Statistic', 'Test Statistic p-value', 'F-Statistic', 'F-Test p-value']
print(dict(zip(labels, white_test)))

Линейная регрессия

In [234]:
formula = "Fingram ~ Age + Income + Среднее_общее_и_ниже + Среднее_специальное + Город"
lin_model_multi = smf.ols(formula = formula, data = regression_data)
lin_model_multi= lin_model_multi.fit()
lin_model_multi.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.137
Model:                            OLS   Adj. R-squared:                  0.137
Method:                 Least Squares   F-statistic:                     373.1
Date:                Wed, 20 Dec 2023   Prob (F-statistic):               0.00
Time:                        00:31:59   Log-Likelihood:                -53364.
No. Observations:               11766   AIC:                         1.067e+05
Df Residuals:                   11760   BIC:                         1.068e+05
Df Model:                           5                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
Intercept               70.1365      0.862     81.377      0.000      68.447      71.826
Age                     -0.0747      0.012     -6.142      0.000      -0.099      -0.051
Income                5.555e-05   7.36e-06      7.551      0.000    4.11e-05       7e-05
Среднее_общее_и_ниже   -14.9860      0.520    -28.824      0.000     -16.005     -13.967
Среднее_специальное     -7.9106      0.579    -13.672      0.000      -9.045      -6.776
Город                   10.0420      0.481     20.886      0.000       9.100      10.984
==============================================================================
Omnibus:                      426.152   Durbin-Watson:                   1.973
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              401.885
Skew:                          -0.405   Prob(JB):                     5.39e-88
Kurtosis:                       2.597   Cond. No.                     1.95e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.95e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

**ВСТРЕЧА С МЕНТОРАМИ -> УСТОЙЧИВОСТЬ МОДЕЛИ НА ПОДВЫБОРКАХ**


In [211]:
regression_data.columns

Index(['index', 'ID', 'Age', 'Age_Group', 'Fingram', 'Income',
       'Высшее_и_неполное_высшее', 'Среднее_общее_и_ниже',
       'Среднее_специальное', 'Город', 'Село', 'ВДОВЕЦ_ВДОВА',
       'НИКОГДА_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ_НЕ_СОСТОЯЛ_А', 'РАЗВЕДЕН_А',
       'СОСТОЮ_В_ЗАРЕГИСТРИРОВАННОМ_БРАКЕ', 'ЖЕНСКИЙ', 'МУЖСКОЙ'],
      dtype='object')

In [212]:
regression_data = regression_data[["Age", "Fingram", "Income", 'Высшее_и_неполное_высшее', 'Среднее_общее_и_ниже', 'Среднее_специальное', "Город", "МУЖСКОЙ", "ЖЕНСКИЙ"]]
regression_data

Age  Fingram  Income  Высшее_и_неполное_высшее  Среднее_общее_и_ниже  \
0       18       43   11000                         0                     0   
1       18       86     930                         0                     1   
2       18       86       0                         1                     0   
3       18       86       0                         0                     1   
4       18       14       0                         0                     1   
...    ...      ...     ...                       ...                   ...   
11761   89       43   20000                         0                     1   
11762   89       57   36400                         1                     0   
11763   89       14   19000                         0                     1   
11764   89       71   25881                         0                     0   
11765   89       29   26000                         0                     1   

       Среднее_специальное  Город  МУЖСКОЙ  ЖЕНСКИЙ  
0                        1      0        1        0  
1                        0      1        1        0  
2                        0      1        0        1  
3                        0      0        0        1  
4                        0      0        0        1  
...                    ...    ...      ...      ...  
11761                    0      1        0        1  
11762                    0      0        0        1  
11763                    0      0        1        0  
11764                    1      1        0        1  
11765                    0      0        0        1  

[11766 rows x 9 columns]

In [213]:
women_regression_data = regression_data[regression_data["ЖЕНСКИЙ"] == 1].drop(["МУЖСКОЙ", "ЖЕНСКИЙ"], axis = 1)
men_regression_data = regression_data[regression_data["МУЖСКОЙ"] == 1].drop(["МУЖСКОЙ", "ЖЕНСКИЙ"], axis = 1)

In [214]:
men_regression_data

Age  Fingram  Income  Высшее_и_неполное_высшее  Среднее_общее_и_ниже  \
0       18       43   11000                         0                     0   
1       18       86     930                         0                     1   
5       18       14    5000                         0                     1   
6       18       14   12000                         0                     1   
8       18       57     600                         0                     1   
...    ...      ...     ...                       ...                   ...   
11745   88       71   19930                         0                     1   
11753   89       71   25000                         1                     0   
11755   89       43   32000                         0                     1   
11759   89       29   32400                         0                     1   
11763   89       14   19000                         0                     1   

       Среднее_специальное  Город  
0                        1      0  
1                        0      1  
5                        0      0  
6                        0      0  
8                        0      1  
...                    ...    ...  
11745                    0      1  
11753                    0      1  
11755                    0      1  
11759                    0      0  
11763                    0      0  

[4916 rows x 7 columns]

In [215]:
women_regression_data

Age  Fingram  Income  Высшее_и_неполное_высшее  Среднее_общее_и_ниже  \
2       18       86       0                         1                     0   
3       18       86       0                         0                     1   
4       18       14       0                         0                     1   
7       18       71       0                         0                     1   
10      18       71     700                         0                     1   
...    ...      ...     ...                       ...                   ...   
11760   89       57   28700                         0                     1   
11761   89       43   20000                         0                     1   
11762   89       57   36400                         1                     0   
11764   89       71   25881                         0                     0   
11765   89       29   26000                         0                     1   

       Среднее_специальное  Город  
2                        0      1  
3                        0      0  
4                        0      0  
7                        0      0  
10                       0      1  
...                    ...    ...  
11760                    0      0  
11761                    0      1  
11762                    0      0  
11764                    1      1  
11765                    0      0  

[6850 rows x 7 columns]

In [216]:
weights = np.polyfit(men_regression_data["Age"], men_regression_data["Fingram"], 2)
model = np.poly1d(weights)
formula = "Fingram ~ model(Age) + Income + Город + Среднее_общее_и_ниже + Среднее_специальное"
poly_model_multi = smf.ols(formula = formula, data = men_regression_data)
poly_model_multi= poly_model_multi.fit()
poly_model_multi.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.149
Model:                            OLS   Adj. R-squared:                  0.148
Method:                 Least Squares   F-statistic:                     171.7
Date:                Tue, 19 Dec 2023   Prob (F-statistic):          8.74e-169
Time:                        22:02:45   Log-Likelihood:                -22302.
No. Observations:                4916   AIC:                         4.462e+04
Df Residuals:                    4910   BIC:                         4.466e+04
Df Model:                           5                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
Intercept               24.2834      9.283      2.616      0.009       6.084      42.483
model(Age)               0.6341      0.140      4.520      0.000       0.359       0.909
Income                5.611e-05   1.03e-05      5.432      0.000    3.59e-05    7.64e-05
Город                   11.1509      0.739     15.097      0.000       9.703      12.599
Среднее_общее_и_ниже   -14.9547      0.836    -17.895      0.000     -16.593     -13.316
Среднее_специальное     -9.0516      0.974     -9.296      0.000     -10.960      -7.143
==============================================================================
Omnibus:                      165.927   Durbin-Watson:                   2.031
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              151.831
Skew:                          -0.377   Prob(JB):                     1.07e-33
Kurtosis:                       2.586   Cond. No.                     1.38e+06
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.38e+06. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

In [217]:
weights = np.polyfit(women_regression_data["Age"], women_regression_data["Fingram"], 2)
model = np.poly1d(weights)
formula = "Fingram ~ model(Age) + Income + Город + Среднее_общее_и_ниже + Среднее_специальное"
poly_model_multi = smf.ols(formula = formula, data = women_regression_data)
poly_model_multi= poly_model_multi.fit()
poly_model_multi.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                Fingram   R-squared:                       0.141
Model:                            OLS   Adj. R-squared:                  0.140
Method:                 Least Squares   F-statistic:                     224.5
Date:                Tue, 19 Dec 2023   Prob (F-statistic):          1.43e-222
Time:                        22:02:54   Log-Likelihood:                -31011.
No. Observations:                6850   AIC:                         6.203e+04
Df Residuals:                    6844   BIC:                         6.207e+04
Df Model:                           5                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
Intercept               15.3604      5.017      3.062      0.002       5.526      25.194
model(Age)               0.7685      0.073     10.465      0.000       0.625       0.913
Income                3.328e-05   1.11e-05      3.012      0.003    1.16e-05    5.49e-05
Город                    9.7746      0.631     15.503      0.000       8.539      11.011
Среднее_общее_и_ниже   -14.7102      0.679    -21.676      0.000     -16.041     -13.380
Среднее_специальное     -7.3670      0.714    -10.312      0.000      -8.767      -5.966
==============================================================================
Omnibus:                      241.654   Durbin-Watson:                   1.989
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              234.018
Skew:                          -0.411   Prob(JB):                     1.53e-51
Kurtosis:                       2.622   Cond. No.                     6.76e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 6.76e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""